In [25]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt

### Current working directory

In [2]:
import os
os.getcwd()

'/home/dsc/Repos/TFM-Test-your-business-viability/TBV_v1'

### Data

Data has been downloaded into working folder:   
- folder2: contains "censo de locales" since 2014


In [22]:
folder2 = '/home/dsc/Repos/TFM-Test-your-business-viability/Data/censolocales/'

!ls -al {folder2}

total 1724088
drwxrwxr-x 2 dsc dsc     4096 oct 13 08:43  .
drwxrwxr-x 3 dsc dsc     4096 oct 13 07:45  ..
-rw-rw-r-- 1 dsc dsc 44416536 oct 13 08:38  2014_10_cla_actividades.csv
-rw-rw-r-- 1 dsc dsc 27343285 oct 13 07:45  2014_10_cla_locales.csv
-rw-rw-r-- 1 dsc dsc      987 oct 13 07:45  campos_fichero_epigrafes
-rw-rw-r-- 1 dsc dsc      881 oct 13 07:45  campos_fichero_locales
-rw-rw-r-- 1 dsc dsc 44849866 oct 13 07:45  cla_actividades201409.csv
-rw-rw-r-- 1 dsc dsc 27459122 oct 13 07:45  cla_locales201409.csv
-rw-rw-r-- 1 dsc dsc  1245108 oct 13 07:45  EpigrafesActividadEconomica.pdf
-rw-rw-r-- 1 dsc dsc   140800 oct 13 07:45  EpigrafesActividadEconomica.xls
-rw-rw-r-- 1 dsc dsc    34507 oct 13 07:45 'Estructura_DS_ FicheroCLA_LICENCIAS.pdf'
-rw-rw-r-- 1 dsc dsc    36129 oct 13 07:45  Estructura_DS_FicheroCLA.pdf
-rw-rw-r-- 1 dsc dsc  4282879 oct 13 08:32  OD_locales1908.csv
-rw-rw-r-- 1 dsc dsc 61010410 oct 13 08:40 'OPEN DATA Licencias201808.csv'
-rw-rw-r-- 1 dsc dsc 63240187 oct

### Sampling with Python
Although files are not so big (<100 MB), I am going to work in chunks to optimize performance
Files are uncompressed.   
Careful with separators: some cleaning through Command Line is necessary to remove "ambigous separators": clean versions of the files   
Encoding is Latin9 although in documentation they talk about UTF8

In [7]:
cd {folder2} #Data folder

/home/dsc/Repos/TFM-Test-your-business-viability/Data/censolocales


In [14]:
ls -l

total 1040460
-rw-rw-r-- 1 dsc dsc 27343285 oct 13 07:45  2014_10_cla_locales.csv
-rw-rw-r-- 1 dsc dsc      987 oct 13 07:45  campos_fichero_epigrafes
-rw-rw-r-- 1 dsc dsc      881 oct 13 07:45  campos_fichero_locales
-rw-rw-r-- 1 dsc dsc 44849866 oct 13 07:45  cla_actividades201409.csv
-rw-rw-r-- 1 dsc dsc 27459122 oct 13 07:45  cla_locales201409.csv
-rw-rw-r-- 1 dsc dsc  1245108 oct 13 07:45  EpigrafesActividadEconomica.pdf
-rw-rw-r-- 1 dsc dsc   140800 oct 13 07:45  EpigrafesActividadEconomica.xls
-rw-rw-r-- 1 dsc dsc    34507 oct 13 07:45 'Estructura_DS_ FicheroCLA_LICENCIAS.pdf'
-rw-rw-r-- 1 dsc dsc    36129 oct 13 07:45  Estructura_DS_FicheroCLA.pdf
-rw-rw-r-- 1 dsc dsc        0 oct 13 08:30  OD_locales1908.csv
-rw-rw-r-- 1 dsc dsc 63240187 oct 13 07:45 'OPEN DATA Licencias201812.csv'
-rw-rw-r-- 1 dsc dsc 67879555 oct 13 07:45 'OPEN DATA Licencias201908.csv'
-rw-rw-r-- 1 dsc dsc 60865638 oct 13 07:45 'OPEN DATA Locales201512.csv'
-rw-rw-r-- 1 dsc dsc 60975971 oct 13 07:45 'OPEN D

In [18]:
%%bash
head -10000 'OPEN DATA Locales201908_clean.csv'> OD_locales1908.csv
head -10000 'OPEN DATA Locales-Epigrafes201908.csv' > OD_epig1908.csv
head -10000

In [ ]:
k = 0

### Files loading

We load the file into memory as a pandas dataframe.   
Let's start examining the data.   
I check all the available files for 201908: locales, licencias and actividades.   
I see the variables: Actividades file (46 columns) includes all the info available in Locales file (40 columns) and Licencias file has additional information about the licence status.   
I start with Actividades file (46 columns) for MPV and I will include licence information just for crossvalidation ('Abierto' vs licence status)   
I will generate a single table, indexed by id_local with of the different year   
For that, I will start analysing a small chunk of the files and when working, I will extend to all the files

In [23]:
cd {folder2}

/home/dsc/Repos/TFM-Test-your-business-viability/Data/censolocales


In [171]:
df_licences19 = pd.read_csv('OPEN DATA Licencias201908.csv',sep=';')
'''licencias_19 variables. 
I check the pdf fields descrition also available in Madrid Opendata
portal'''
pd_licences19.info()

/home/dsc/.local/lib/python3.7/site-packages/IPython/core/interactiveshell.py:3057: DtypeWarning: Columns (41,43) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 121257 entries, 0 to 121256
Data columns (total 46 columns):
id_local                        121257 non-null int64
id_distrito_local               121257 non-null int64
desc_distrito_local             121257 non-null object
id_barrio_local                 121257 non-null int64
desc_barrio_local               121257 non-null object
cod_barrio_local                121257 non-null int64
id_seccion_censal_local         121257 non-null int64
desc_seccion_censal_local       121257 non-null int64
coordenada_x_local              121257 non-null object
coordenada_y_local              121257 non-null object
id_tipo_acceso_local            121257 non-null int64
desc_tipo_acceso_local          121257 non-null object
id_situacion_local              121257 non-null int64
desc_situacion_local            121257 non-null object
id_ndp_edificio                 121257 non-null int64
id_clase_ndp_edificio           121257 non-null int64
id_vial_edificio   

In [72]:
#same with locales
df_locales19 = pd.read_csv('OPEN DATA Locales201908_clean.csv',sep=';')
df_locales19.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 147318 entries, 0 to 147317
Data columns (total 40 columns):
id_local                     147318 non-null int64
id_distrito_local            147318 non-null int64
desc_distrito_local          147318 non-null object
id_barrio_local              147318 non-null int64
desc_barrio_local            147318 non-null object
cod_barrio_local             0 non-null float64
id_seccion_censal_local      0 non-null float64
desc_seccion_censal_local    147318 non-null int64
coordenada_x_local           147318 non-null object
coordenada_y_local           147318 non-null object
id_tipo_acceso_local         0 non-null float64
desc_tipo_acceso_local       147318 non-null object
id_situacion_local           147318 non-null int64
desc_situacion_local         147318 non-null object
id_vial_edificio             0 non-null float64
clase_vial_edificio          147318 non-null object
desc_vial_edificio           147318 non-null object
id_ndp_edificio           

In [70]:
#same with Epigrafes = Actividades
df_epi19 = pd.read_csv('OPEN DATA Locales-Epigrafes201908.csv',sep=';',encoding='latin9')
df_epi19.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 163316 entries, 0 to 163315
Data columns (total 46 columns):
id_local                     163316 non-null int64
id_distrito_local            163316 non-null int64
desc_distrito_local          163316 non-null object
id_barrio_local              163316 non-null int64
desc_barrio_local            163316 non-null object
cod_barrio_local             0 non-null float64
id_seccion_censal_local      0 non-null float64
desc_seccion_censal_local    163316 non-null int64
coordenada_x_local           163316 non-null object
coordenada_y_local           163316 non-null object
id_tipo_acceso_local         0 non-null float64
desc_tipo_acceso_local       163316 non-null object
id_situacion_local           0 non-null float64
desc_situacion_local         163316 non-null object
id_vial_edificio             163316 non-null int64
clase_vial_edificio          163316 non-null object
desc_vial_edificio           163316 non-null object
id_ndp_edificio           

I see the variables: Actividades file (46 columns) includes all the info available in Locales file (40 columns) and Licencias file has additional information about the licence status.
I would start with Actividades file (46 columns) for MPV and I will include licence information just for crossvalidation ('Abierto' vs licence status). Previously, I am going to make a final check len(locales) vs len(epigrafes) just to be sure I am not leaving out some important reference

In [74]:
len(df_locales19) - len(df_epi19)

-15998

In [87]:
len(df_epi19['id_local'].unique())

147317

In [91]:
len(df_epi19)-len(df_epi19['id_local'].unique())

15999

In [89]:
len(df_locales19['id_local'].unique())

147318

In [112]:
df2 = df_epi19[df_epi19['id_local'].duplicated()]
df2[df2['id_barrio_local'] == 201]

id_local  id_distrito_local   desc_distrito_local  id_barrio_local  \
5878    285005494                  2  ARGANZUELA                        201   
17651   270515381                  2  ARGANZUELA                        201   
23946   280016500                  2  ARGANZUELA                        201   
23973   280016612                  2  ARGANZUELA                        201   
24268   280018125                  2  ARGANZUELA                        201   
35694    20000182                  2  ARGANZUELA                        201   
35984    20000184                  2  ARGANZUELA                        201   
36303    20000179                  2  ARGANZUELA                        201   
36304    20000182                  2  ARGANZUELA                        201   
36600    20001334                  2  ARGANZUELA                        201   
36753    20001955                  2  ARGANZUELA                        201   
43397    20000182                  2  ARGANZUELA                        201   
43406    20000344                  2  ARGANZUELA                        201   
43408    20000357                  2  ARGANZUELA                        201   
47168   270054004                  2  ARGANZUELA                        201   
47739   270054004                  2  ARGANZUELA                        201   
47740   270054004                  2  ARGANZUELA                        201   
48926   270041789                  2  ARGANZUELA                        201   
49308    20001056                  2  ARGANZUELA                        201   
49597   270053995                  2  ARGANZUELA                        201   
49600   270054179                  2  ARGANZUELA                        201   
49615   270054434                  2  ARGANZUELA                        201   
55540    20001326                  2  ARGANZUELA                        201   
56121   270244515                  2  ARGANZUELA                        201   
57636   270302934                  2  ARGANZUELA                        201   
57726   270244515                  2  ARGANZUELA                        201   
59230   270320023                  2  ARGANZUELA                        201   
59231   270320023                  2  ARGANZUELA                        201   
59312   270302934                  2  ARGANZUELA                        201   
59313   270302934                  2  ARGANZUELA                        201   
...           ...                ...                   ...              ...   
135229  270299714                  2  ARGANZUELA                        201   
135284  270302934                  2  ARGANZUELA                        201   
135285  270302934                  2  ARGANZUELA                        201   
135515  270309268                  2  ARGANZUELA                        201   
135726  270320023                  2  ARGANZUELA                        201   
135727  270320023                  2  ARGANZUELA                        201   
135995  270347318                  2  ARGANZUELA                        201   
137423  270421033                  2  ARGANZUELA                        201   
138478  270482191                  2  ARGANZUELA                        201   
138488  270482579                  2  ARGANZUELA                        201   
138631  270489404                  2  ARGANZUELA                        201   
138970  270420894                  2  ARGANZUELA                        201   
139651  270522243                  2  ARGANZUELA                        201   
139656  270522271                  2  ARGANZUELA                        201   
140362  270529815                  2  ARGANZUELA                        201   
145966  280016500                  2  ARGANZUELA                        201   
145975  280016548                  2  ARGANZUELA                        201   
145983  280016591                  2  ARGANZUELA                        201   
145992  280016628                  2  ARGANZUELA           

In [120]:
df_epi19[df_epi19['id_local'] == 20000182]

id_local  id_distrito_local   desc_distrito_local  id_barrio_local  \
35693  20000182                  2  ARGANZUELA                        201   
35694  20000182                  2  ARGANZUELA                        201   
36304  20000182                  2  ARGANZUELA                        201   
43397  20000182                  2  ARGANZUELA                        201   

          desc_barrio_local  cod_barrio_local  id_seccion_censal_local  \
35693  IMPERIAL                           NaN                      NaN   
35694  IMPERIAL                           NaN                      NaN   
36304  IMPERIAL                           NaN                      NaN   
43397  IMPERIAL                           NaN                      NaN   

       desc_seccion_censal_local coordenada_x_local coordenada_y_local  \
35693                         14          439566,59         4473090,53   
35694                         14          439566,59         4473090,53   
36304                         14          439566,59         4473090,53   
43397                         14          439566,59         4473090,53   

       id_tipo_acceso_local desc_tipo_acceso_local  id_situacion_local  \
35693                   NaN           Puerta Calle                 NaN   
35694                   NaN           Puerta Calle                 NaN   
36304                   NaN           Puerta Calle                 NaN   
43397                   NaN           Puerta Calle                 NaN   

      desc_situacion_local  id_vial_edificio       clase_vial_edificio  \
35693              Abierto            615000  GLORIETA                   
35694              Abierto            615000  GLORIETA                   
36304              Abierto            615000  GLORIETA                   
43397              Abierto            615000  GLORIETA                   

                                      desc_vial_edificio  id_ndp_edificio  \
35693  PUERTA DE TOLEDO                              ...         11008266   
35694  PUERTA DE TOLEDO                              ...         11008266   
36304  PUERTA DE TOLEDO                              ...         11008266   
43397  PUERTA DE TOLEDO                              ...         11008266   

       id_clase_ndp_edificio nom_edificio  num_edificio cal_edificio  \
35693                      1          NUM             4                
35694                      1          NUM             4                
36304                      1          NUM             4                
43397                      1          NUM             4                

       secuencial_local_PC  id_vial_acceso         clase_vial_acceso  \
35693                   10             NaN  GLORIETA                   
35694                   10             NaN  GLORIETA                   
36304                   10             NaN  GLORIETA                   
43397                   10             NaN  GLORIETA                   

                                        desc_vial_acceso  id_ndp_acceso  \
35693  PUERTA DE TOLEDO                              ...       11008266   
35694  PUERTA DE TOLEDO                              ...       11008266   
36304  PUERTA DE TOLEDO                              ...       11008266   
43397  PUERTA DE TOLEDO                              ...       11008266   

       id_clase_ndp_acceso nom_acceso  num_acceso cal_acceso  \
35693                    1        NUM           4              
35694                    1        NUM           4              
36304                    1        NUM           4              
43397                    1        NUM           4              

      coordenada_x_agrupacion coordenada_y_agrup  id_agrupacion  \
35693                     NaN                NaN            NaN   
35694                     NaN                NaN            NaN   
36304                     NaN                NaN            NaN   
43397                     NaN                NaN            NaN 

In [116]:
pd.set_option('display.max_column',None)

Los mismos locales puedes estar dados de alta con diferentes épigrafes/actividades. Ej: un local puede estar dado de alta como restaurante y como comercio al por menor de pasteleria&pan   
En la primera versión voy a dejar todas las referencias y en función de los '1' y '0' que salgan, tomaré decisiones sobre estos

In [121]:
'''aunque aparentemente Epigrafes es el mismo fichero que locales 
ampliado, parece que hay una referencia en locales que no está en
epigrafes. Voy a buscarla para ver en qué casos se da esta 
situación.
Además compruebo que locales si que tiene identificadores únicos'''
len(df_locales19), len(df_locales19['id_local'].unique())

(147318, 147318)

Hay un identificador de diferencia entre el fichero de locales y el de epigrafes (uno más en locales). Hago un bucle para identificarlo. Tarda mucho (la próxima vez buscaré hacerlo con un merge/concat pero esta vez no se me ha ocurrido).
He identificado que el id_local 80001076 está en fichero de locales y no en el de epígrafes. Como es una cadena conocida. Lo completaré con los mismo datos que tenga en epígrafes en otros sitios de la misma cadena.

In [164]:
%%time
k = 0
falta = []
for i in df_locales19['id_local'].unique():
    if i in df_epi19['id_local'].unique():
        k += 1
        print(k, True, i)
    else:
        falta.append(i)
print(k,falta)

1 True 280018574
2 True 280018581
3 True 280018584
4 True 280018586
5 True 280018588
6 True 280018590
7 True 280018593
8 True 280018594
9 True 280018609
10 True 280018614
11 True 280018617
12 True 280018622
13 True 280018624
14 True 280018638
15 True 280018643
16 True 280018645
17 True 280018654
18 True 280018662
19 True 280018668
20 True 280018672
21 True 280018673
22 True 280018675
23 True 280018677
24 True 280018680
25 True 280018683
26 True 280018687
27 True 280018689
28 True 280018690
29 True 280018691
30 True 280019333
31 True 280019337
32 True 280019344
33 True 280019355
34 True 280019361
35 True 280019366
36 True 280019369
37 True 280019370
38 True 280019372
39 True 280019383
40 True 280019384
41 True 280019385
42 True 280019387
43 True 280019388
44 True 280019389
45 True 280019393
46 True 280019395
47 True 280019402
48 True 280019405
49 True 280019407
50 True 280019410
51 True 280019413
52 True 280019414
53 True 280019418
54 True 280019422
55 True 280019423
56 True 280019427
5

453 True 280021643
454 True 280021645
455 True 280021653
456 True 280021660
457 True 280021663
458 True 280021678
459 True 280021679
460 True 280021681
461 True 280021692
462 True 280021694
463 True 280021699
464 True 280021727
465 True 280021733
466 True 280021734
467 True 280021738
468 True 280021741
469 True 280021754
470 True 280021755
471 True 280021765
472 True 280021766
473 True 280021781
474 True 280021787
475 True 280021788
476 True 280021791
477 True 280021792
478 True 280021799
479 True 280021803
480 True 280021805
481 True 280021807
482 True 280021810
483 True 280021816
484 True 280021823
485 True 280021826
486 True 280021828
487 True 280021831
488 True 280021832
489 True 280021838
490 True 280021840
491 True 280021841
492 True 280021843
493 True 280021844
494 True 280021845
495 True 280021847
496 True 280021849
497 True 280021851
498 True 280021853
499 True 280021854
500 True 280021855
501 True 280021859
502 True 280021862
503 True 280021864
504 True 280021869
505 True 280

901 True 280023818
902 True 280023820
903 True 280023823
904 True 280023824
905 True 280023838
906 True 280023839
907 True 280023842
908 True 280023843
909 True 280023864
910 True 280023868
911 True 280023872
912 True 280023875
913 True 280023877
914 True 280023880
915 True 280023883
916 True 280023895
917 True 280023900
918 True 280023901
919 True 280023903
920 True 280023913
921 True 280023919
922 True 280023931
923 True 280023934
924 True 280023936
925 True 280023939
926 True 280023947
927 True 280023954
928 True 280023959
929 True 280023963
930 True 280023974
931 True 280023980
932 True 280023986
933 True 280023990
934 True 280024007
935 True 280024010
936 True 280024012
937 True 280024014
938 True 280024017
939 True 280024025
940 True 280024027
941 True 280024033
942 True 280024040
943 True 280024043
944 True 280024047
945 True 280024053
946 True 280024054
947 True 280024059
948 True 280024066
949 True 280024069
950 True 280024114
951 True 280024179
952 True 280024792
953 True 280

1336 True 280030122
1337 True 280030129
1338 True 280030133
1339 True 280030136
1340 True 280030139
1341 True 280030146
1342 True 280030148
1343 True 280030149
1344 True 280030157
1345 True 280030162
1346 True 280030165
1347 True 280030168
1348 True 280030171
1349 True 280030173
1350 True 280030180
1351 True 280030192
1352 True 280030194
1353 True 280030198
1354 True 280030199
1355 True 280030203
1356 True 280030208
1357 True 280030217
1358 True 280030222
1359 True 280030230
1360 True 280030232
1361 True 280030236
1362 True 280030245
1363 True 280030247
1364 True 280030248
1365 True 280030253
1366 True 280030260
1367 True 280030263
1368 True 280030266
1369 True 280030270
1370 True 280030271
1371 True 280030272
1372 True 280030283
1373 True 280030286
1374 True 280030287
1375 True 280030293
1376 True 280030295
1377 True 280030302
1378 True 280030307
1379 True 280030309
1380 True 280030310
1381 True 280030346
1382 True 280030352
1383 True 280030353
1384 True 280030355
1385 True 280030360


1773 True 280032154
1774 True 280032155
1775 True 280032162
1776 True 280032167
1777 True 280032177
1778 True 280032184
1779 True 280032185
1780 True 280032209
1781 True 280032214
1782 True 280032215
1783 True 280032216
1784 True 280032220
1785 True 280032229
1786 True 280032231
1787 True 280032234
1788 True 280032248
1789 True 280032254
1790 True 280032261
1791 True 280032266
1792 True 280032274
1793 True 280032279
1794 True 280032294
1795 True 280032298
1796 True 280032306
1797 True 280032307
1798 True 280032323
1799 True 280032326
1800 True 280032329
1801 True 280032333
1802 True 280032340
1803 True 280032343
1804 True 280032345
1805 True 280032349
1806 True 280032354
1807 True 280032358
1808 True 280032362
1809 True 280032363
1810 True 280032368
1811 True 280032372
1812 True 280032373
1813 True 280032390
1814 True 280032391
1815 True 280032393
1816 True 280032402
1817 True 280032406
1818 True 280032415
1819 True 280032422
1820 True 280032424
1821 True 280032428
1822 True 280032429


...

145620 True 290000542
145621 True 290000543
145622 True 290000552
145623 True 290000557
145624 True 290000565
145625 True 290000572
145626 True 290000573
145627 True 290000576
145628 True 290000577
145629 True 290000578
145630 True 290000583
145631 True 290000589
145632 True 290000591
145633 True 290000592
145634 True 290000598
145635 True 290000600
145636 True 290000610
145637 True 290000613
145638 True 290000617
145639 True 290000618
145640 True 290000621
145641 True 290000635
145642 True 290000636
145643 True 290000640
145644 True 290000641
145645 True 290000644
145646 True 290000653
145647 True 290000656
145648 True 290000658
145649 True 290000662
145650 True 290000668
145651 True 290000669
145652 True 290000671
145653 True 290000675
145654 True 290000686
145655 True 290000689
145656 True 290000690
145657 True 290000698
145658 True 290000702
145659 True 290000707
145660 True 290000709
145661 True 290000712
145662 True 290000715
145663 True 290000722
145664 True 290000723
145665 Tru

146004 True 285043493
146005 True 285043494
146006 True 285043497
146007 True 285043502
146008 True 285043505
146009 True 285043507
146010 True 285043515
146011 True 285043518
146012 True 285043522
146013 True 285043529
146014 True 285043531
146015 True 285043535
146016 True 285043540
146017 True 285043542
146018 True 285043551
146019 True 285043557
146020 True 285043564
146021 True 285043572
146022 True 285043574
146023 True 285043588
146024 True 285043589
146025 True 285043594
146026 True 285043596
146027 True 285043597
146028 True 285043609
146029 True 285043616
146030 True 285043619
146031 True 285043621
146032 True 285043622
146033 True 285043625
146034 True 285043626
146035 True 285043629
146036 True 285043634
146037 True 285043637
146038 True 285043652
146039 True 285043657
146040 True 285043658
146041 True 285043660
146042 True 285043664
146043 True 285043666
146044 True 285043668
146045 True 285043672
146046 True 285043691
146047 True 285043693
146048 True 285043694
146049 Tru

146389 True 285045099
146390 True 285045110
146391 True 285045114
146392 True 285045115
146393 True 285045120
146394 True 285045121
146395 True 285045122
146396 True 285045126
146397 True 285045127
146398 True 285045130
146399 True 285045139
146400 True 285045141
146401 True 285045143
146402 True 285045148
146403 True 285045157
146404 True 285045158
146405 True 285045163
146406 True 285045167
146407 True 285045172
146408 True 285045177
146409 True 285045181
146410 True 285045185
146411 True 285045187
146412 True 285045190
146413 True 285045193
146414 True 285045196
146415 True 285045199
146416 True 285045205
146417 True 285045211
146418 True 285045212
146419 True 285045220
146420 True 285045224
146421 True 285045228
146422 True 285045229
146423 True 285045232
146424 True 285045237
146425 True 285045238
146426 True 285045239
146427 True 285045240
146428 True 285045241
146429 True 285045249
146430 True 285045258
146431 True 285045269
146432 True 285045273
146433 True 285045276
146434 Tru

146771 True 285046570
146772 True 285046572
146773 True 285046573
146774 True 285046574
146775 True 285046580
146776 True 285046586
146777 True 285046593
146778 True 285046599
146779 True 285046600
146780 True 285046605
146781 True 285046606
146782 True 285046610
146783 True 285046614
146784 True 285046616
146785 True 285046628
146786 True 285046631
146787 True 285046635
146788 True 285046642
146789 True 285046646
146790 True 285046649
146791 True 285046653
146792 True 285046654
146793 True 285046656
146794 True 285046659
146795 True 285046664
146796 True 285046667
146797 True 285046669
146798 True 285046677
146799 True 285046678
146800 True 285046684
146801 True 285046688
146802 True 285046689
146803 True 285046692
146804 True 285046697
146805 True 285046701
146806 True 285046703
146807 True 285046704
146808 True 285046705
146809 True 285046709
146810 True 285046710
146811 True 285046712
146812 True 285046713
146813 True 285046714
146814 True 285046716
146815 True 285046719
146816 Tru

147161 True 290001013
147162 True 290001021
147163 True 290001030
147164 True 290001031
147165 True 290001037
147166 True 290001039
147167 True 290001040
147168 True 290001041
147169 True 290001052
147170 True 290001054
147171 True 290001055
147172 True 290001057
147173 True 290001061
147174 True 290001063
147175 True 290001068
147176 True 290001069
147177 True 290001070
147178 True 290001071
147179 True 290001075
147180 True 290001077
147181 True 290001079
147182 True 290001081
147183 True 290001086
147184 True 290001093
147185 True 290001099
147186 True 290001101
147187 True 290001105
147188 True 290001107
147189 True 290001110
147190 True 290001117
147191 True 290001121
147192 True 290001126
147193 True 290001131
147194 True 290001135
147195 True 290001136
147196 True 290001141
147197 True 290001143
147198 True 290001146
147199 True 290001152
147200 True 290001163
147201 True 290001166
147202 True 290001168
147203 True 290001171
147204 True 290001172
147205 True 290001175
147206 Tru

In [165]:
df_locales19[df_locales19['id_local'] == 80001076]

id_local  id_distrito_local   desc_distrito_local  id_barrio_local  \
54437  80001076                  8  FUENCARRAL-EL PARDO               804   

          desc_barrio_local  cod_barrio_local  id_seccion_censal_local  \
54437  EL PILAR                           NaN                      NaN   

       desc_seccion_censal_local coordenada_x_local coordenada_y_local  \
54437                         45          440241,62         4481242,55   

       id_tipo_acceso_local desc_tipo_acceso_local  id_situacion_local  \
54437                   NaN               Agrupado                   1   

      desc_situacion_local  id_vial_edificio       clase_vial_edificio  \
54437              Abierto               NaN  AVENIDA                    

                                      desc_vial_edificio  id_ndp_edificio  \
54437  MONFORTE DE LEMOS                             ...         20095319   

       id_clase_ndp_edificio nom_edificio  num_edificio cal_edificio  \
54437                      1          NUM            30                

       secuencial_local_PC  id_vial_acceso         clase_vial_acceso  \
54437                    0             NaN  AVENIDA                    

                                        desc_vial_acceso  id_ndp_acceso  \
54437  MONFORTE DE LEMOS                             ...       31049013   

       id_clase_ndp_acceso nom_acceso  num_acceso cal_acceso  \
54437                    1        NUM          36              

      coordenada_x_agrupacion coordenada_y_agrup  id_agrupacion  \
54437               440241,62         4481242,55     99000109.0   

                 nombre_agrupacion  id_tipo_agrup   desc_tipo_agrup  \
54437  CENTRO COMERCIAL LA VAGUADA            1.0  Centro Comercial   

      id_planta_agrupado id_local_agrupado         rotulo  
54437                  2                23  CAÑAS Y TAPAS

In [169]:
vaguada = df_epi19[df_epi19['nombre_agrupacion'] == 'CENTRO COMERCIAL LA VAGUADA']
vaguada[vaguada['rotulo'] == 'CAÑAS Y TAPAS']

Empty DataFrame
Columns: [id_local, id_distrito_local, desc_distrito_local, id_barrio_local, desc_barrio_local, cod_barrio_local, id_seccion_censal_local, desc_seccion_censal_local, coordenada_x_local, coordenada_y_local, id_tipo_acceso_local, desc_tipo_acceso_local, id_situacion_local, desc_situacion_local, id_vial_edificio, clase_vial_edificio, desc_vial_edificio, id_ndp_edificio, id_clase_ndp_edificio, nom_edificio, num_edificio, cal_edificio, secuencial_local_PC, id_vial_acceso, clase_vial_acceso, desc_vial_acceso, id_ndp_acceso, id_clase_ndp_acceso, nom_acceso, num_acceso, cal_acceso, coordenada_x_agrupacion, coordenada_y_agrup, id_agrupacion, nombre_agrupacion, id_tipo_agrup, desc_tipo_agrup, id_planta_agrupado, id_local_agrupado, rotulo, id_seccion, desc_seccion, id_division, desc_division, id_epigrafe, desc_epigrafe]
Index: []

In [172]:
df_licences19[df_licences19['id_local']==80001076]

id_local  id_distrito_local   desc_distrito_local  id_barrio_local  \
8615  80001076                  8  FUENCARRAL-EL PARDO               804   
8616  80001076                  8  FUENCARRAL-EL PARDO               804   
8617  80001076                  8  FUENCARRAL-EL PARDO               804   

         desc_barrio_local  cod_barrio_local  id_seccion_censal_local  \
8615  EL PILAR                             4                     8045   
8616  EL PILAR                             4                     8045   
8617  EL PILAR                             4                     8045   

      desc_seccion_censal_local coordenada_x_local coordenada_y_local  \
8615                         45          440241,62         4481242,55   
8616                         45          440241,62         4481242,55   
8617                         45          440241,62         4481242,55   

      id_tipo_acceso_local desc_tipo_acceso_local  id_situacion_local  \
8615                     0               Agrupado                   1   
8616                     0               Agrupado                   1   
8617                     0               Agrupado                   1   

     desc_situacion_local  id_ndp_edificio  id_clase_ndp_edificio  \
8615              Abierto         20095319                      1   
8616              Abierto         20095319                      1   
8617              Abierto         20095319                      1   

      id_vial_edificio       clase_vial_edificio  \
8615            514425  AVENIDA                    
8616            514425  AVENIDA                    
8617            514425  AVENIDA                    

                                     desc_vial_edificio nom_edificio  \
8615  MONFORTE DE LEMOS                             ...          NUM   
8616  MONFORTE DE LEMOS                             ...          NUM   
8617  MONFORTE DE LEMOS                             ...          NUM   

      num_edificio cal_edificio  secuencial_local_PC  id_ndp_acceso  \
8615            30                                 0       31049013   
8616            30                                 0       31049013   
8617            30                                 0       31049013   

      id_clase_ndp_acceso  id_vial_acceso         clase_vial_acceso  \
8615                    1          514425  AVENIDA                    
8616                    1          514425  AVENIDA                    
8617                    1          514425  AVENIDA                    

                                       desc_vial_acceso nom_acceso  \
8615  MONFORTE DE LEMOS                             ...        NUM   
8616  MONFORTE DE LEMOS                             ...        NUM   
8617  MONFORTE DE LEMOS                             ...        NUM   

      num_acceso cal_acceso coordenada_x_agrupacion coordenada_y_agrupacion  \
8615          36                          440241,62              4481242,55   
8616          36                          440241,62              4481242,55   
8617          36                          440241,62              4481242,55   

      id_agrupacion            nombre_agrupacion  id_tipo_agrup  \
8615       99000109  CENTRO COMERCIAL LA VAGUADA              1   
8616       99000109  CENTRO COMERCIAL LA VAGUADA              1   
8617       99000109  CENTRO COMERCIAL LA VAGUADA              1   

       desc_tipo_agrup id_planta_agrupado id_local_agrupado         rotulo  \
8615  Centro Comercial                  2                23  CAÑAS Y TAPAS   
8616  Centro Comercial                  2                23  CAÑAS Y TAPAS   
8617  Centro Comercial                  2                23  CAÑAS Y TAPAS   

        ref_licencia id_tipo_licencia                   desc_tipo_licencia  \
8615  108/2005/03627                2                 Licencia Urbanística   
8616  500/2017/01184                1              Declaración Responsable   
8617  500/2017/03926                4  Transmisión de licencia 

In [269]:
df_epi19.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 163316 entries, 0 to 163315
Data columns (total 46 columns):
id_local                     163316 non-null int64
id_distrito_local            163316 non-null int64
desc_distrito_local          163316 non-null object
id_barrio_local              163316 non-null int64
desc_barrio_local            163316 non-null object
cod_barrio_local             0 non-null float64
id_seccion_censal_local      0 non-null float64
desc_seccion_censal_local    163316 non-null int64
coordenada_x_local           163316 non-null object
coordenada_y_local           163316 non-null object
id_tipo_acceso_local         0 non-null float64
desc_tipo_acceso_local       163316 non-null object
id_situacion_local           0 non-null float64
desc_situacion_local         163316 non-null object
id_vial_edificio             163316 non-null int64
clase_vial_edificio          163316 non-null object
desc_vial_edificio           163316 non-null object
id_ndp_edificio           

In [270]:
df_locales19.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 147318 entries, 0 to 147317
Data columns (total 40 columns):
id_local                     147318 non-null int64
id_distrito_local            147318 non-null int64
desc_distrito_local          147318 non-null object
id_barrio_local              147318 non-null int64
desc_barrio_local            147318 non-null object
cod_barrio_local             0 non-null float64
id_seccion_censal_local      0 non-null float64
desc_seccion_censal_local    147318 non-null int64
coordenada_x_local           147318 non-null object
coordenada_y_local           147318 non-null object
id_tipo_acceso_local         0 non-null float64
desc_tipo_acceso_local       147318 non-null object
id_situacion_local           147318 non-null int64
desc_situacion_local         147318 non-null object
id_vial_edificio             0 non-null float64
clase_vial_edificio          147318 non-null object
desc_vial_edificio           147318 non-null object
id_ndp_edificio           

Tras revisar los nulos, reviso un registros en ambos ficheros para ver la pinta que tiene y decidir las variables con las que me quedo

In [276]:
df_epi19[df_epi19['id_local'] == 280052883]

id_local  id_distrito_local   desc_distrito_local  id_barrio_local  \
0  280052883                 11  CARABANCHEL                      1102   

      desc_barrio_local  cod_barrio_local  id_seccion_censal_local  \
0  OPAÑEL                             NaN                      NaN   

   desc_seccion_censal_local coordenada_x_local coordenada_y_local  \
0                         22          439084,59         4471128,53   

   id_tipo_acceso_local desc_tipo_acceso_local  id_situacion_local  \
0                   NaN           Puerta Calle                 NaN   

  desc_situacion_local  id_vial_edificio       clase_vial_edificio  \
0              Abierto             75700  CALLE                      

                                  desc_vial_edificio  id_ndp_edificio  \
0  ARROYO OPAÑEL                                 ...         11069749   

   id_clase_ndp_edificio nom_edificio  num_edificio cal_edificio  \
0                      1          NUM            10                

   secuencial_local_PC  id_vial_acceso         clase_vial_acceso  \
0                   40             NaN  CALLE                      

                                    desc_vial_acceso  id_ndp_acceso  \
0  ARROYO OPAÑEL                                 ...       11069749   

   id_clase_ndp_acceso nom_acceso  num_acceso cal_acceso  \
0                    1        NUM          10              

  coordenada_x_agrupacion coordenada_y_agrup  id_agrupacion nombre_agrupacion  \
0                     NaN                NaN            NaN               NaN   

   id_tipo_agrup desc_tipo_agrup id_planta_agrupado id_local_agrupado  \
0            NaN             NaN                 PB               NaN   

              rotulo id_seccion  \
0  TALLER AUTOMASTER          G   

                                        desc_seccion id_division  \
0  COMERCIO AL POR MAYOR Y AL POR MENOR; REPARACI...          45   

                                       desc_division id_epigrafe  \
0  VENTA Y REPARACI0N DE VEHICULOS DE MOTOR Y MOT...      452002   

                                       desc_epigrafe  
0  TALLER DE REPARACION DE AUTOMOVILES ESPECIALIZ...

In [275]:
df_locales19[df_locales19['id_local'] == 280052883]

id_local  id_distrito_local   desc_distrito_local  id_barrio_local  \
98170  280052883                 11  CARABANCHEL                      1102   

          desc_barrio_local  cod_barrio_local  id_seccion_censal_local  \
98170  OPAÑEL                             NaN                      NaN   

       desc_seccion_censal_local coordenada_x_local coordenada_y_local  \
98170                         22          439084,59         4471128,53   

       id_tipo_acceso_local desc_tipo_acceso_local  id_situacion_local  \
98170                   NaN           Puerta Calle                   1   

      desc_situacion_local  id_vial_edificio       clase_vial_edificio  \
98170              Abierto               NaN  CALLE                      

                                      desc_vial_edificio  id_ndp_edificio  \
98170  ARROYO OPAÑEL                                 ...         11069749   

       id_clase_ndp_edificio nom_edificio  num_edificio cal_edificio  \
98170                      1          NUM            10                

       secuencial_local_PC  id_vial_acceso         clase_vial_acceso  \
98170                   40             NaN  CALLE                      

                                        desc_vial_acceso  id_ndp_acceso  \
98170  ARROYO OPAÑEL                                 ...       11069749   

       id_clase_ndp_acceso nom_acceso  num_acceso cal_acceso  \
98170                    1        NUM          10              

      coordenada_x_agrupacion coordenada_y_agrup  id_agrupacion  \
98170                     NaN                NaN            NaN   

      nombre_agrupacion  id_tipo_agrup desc_tipo_agrup id_planta_agrupado  \
98170               NaN            NaN             NaN                 PB   

      id_local_agrupado             rotulo  
98170               NaN  TALLER AUTOMASTER

In [286]:
df_locales19.columns

Index(['id_local', 'id_distrito_local', 'desc_distrito_local',
       'id_barrio_local', 'desc_barrio_local', 'cod_barrio_local',
       'id_seccion_censal_local', 'desc_seccion_censal_local',
       'coordenada_x_local', 'coordenada_y_local', 'id_tipo_acceso_local',
       'desc_tipo_acceso_local', 'id_situacion_local', 'desc_situacion_local',
       'id_vial_edificio', 'clase_vial_edificio', 'desc_vial_edificio',
       'id_ndp_edificio', 'id_clase_ndp_edificio', 'nom_edificio',
       'num_edificio', 'cal_edificio', 'secuencial_local_PC', 'id_vial_acceso',
       'clase_vial_acceso', 'desc_vial_acceso', 'id_ndp_acceso',
       'id_clase_ndp_acceso', 'nom_acceso', 'num_acceso', 'cal_acceso',
       'coordenada_x_agrupacion', 'coordenada_y_agrup', 'id_agrupacion',
       'nombre_agrupacion', 'id_tipo_agrup', 'desc_tipo_agrup',
       'id_planta_agrupado', 'id_local_agrupado', 'rotulo'],
      dtype='object')

In [287]:
df_epi19.columns

Index(['id_local', 'id_distrito_local', 'desc_distrito_local',
       'id_barrio_local', 'desc_barrio_local', 'cod_barrio_local',
       'id_seccion_censal_local', 'desc_seccion_censal_local',
       'coordenada_x_local', 'coordenada_y_local', 'id_tipo_acceso_local',
       'desc_tipo_acceso_local', 'id_situacion_local', 'desc_situacion_local',
       'id_vial_edificio', 'clase_vial_edificio', 'desc_vial_edificio',
       'id_ndp_edificio', 'id_clase_ndp_edificio', 'nom_edificio',
       'num_edificio', 'cal_edificio', 'secuencial_local_PC', 'id_vial_acceso',
       'clase_vial_acceso', 'desc_vial_acceso', 'id_ndp_acceso',
       'id_clase_ndp_acceso', 'nom_acceso', 'num_acceso', 'cal_acceso',
       'coordenada_x_agrupacion', 'coordenada_y_agrup', 'id_agrupacion',
       'nombre_agrupacion', 'id_tipo_agrup', 'desc_tipo_agrup',
       'id_planta_agrupado', 'id_local_agrupado', 'rotulo', 'id_seccion',
       'desc_seccion', 'id_division', 'desc_division', 'id_epigrafe',
       'desc_epi

Comparando las variables:    
- ni en df_epi19 ni en df_locales19 tengo valores de: "cod_barrio_local", "id_seccion_censal_local", "id_tipo_acceso_local", "id_vial_acceso" -> eliminaré las columnas. No son relevantes para este ejercicio
- en df_locales19 no tengo valores de "id_vial_edificio", sí lo tengo en df_epi19 -> me quedaré con los datos de fichero de epigrafes pero si me da problemas, lo eliminaré (no parecen relevantes para el estudio. Lo hago para no perder información).
- en df_epi19 no tengo valores de "id_situacion_local" -> me quedaré con los datos de df_locales19 y veré si coincide 
- quitaré la columnas cal_acceso (no tiene porqué aparecer siempre)
- los datos de agrupación los cogeré de df_epi19 (tiene más valores): completaré la columnas 'id_tipo_agrup' con -1 y 'nombre_agrupacion' y 'desc_tipo_agrup' con 'SIN AGRUPACION' y el resto haré un drop: 'id_agrupacion', 'id_planta_agrupado', 'id_local_agrupado y las coordenadas

En resumen:   
- df_locales19: drop columns: 'cod_barrio_local','id_seccion_censal_local','id_tipo_acceso_local', 'id_vial_acceso','id_vial_edificio', 'coordenada_x_agrupacion', 'coordenada_y_agrup','id_agrupacion','nombre_agrupacion', 'id_tipo_agrup', 'desc_tipo_agrup', 'id_planta_agrupado', 'id_local_agrupado', 'cal_acceso'
- df_epi19: drop columns: 'id_distrito_local', 'desc_distrito_local', 'id_barrio_local', 'desc_barrio_local', 'cod_barrio_local','id_seccion_censal_local','desc_seccion_censal_local','coordenada_x_local', 'coordenada_y_local','id_tipo_acceso_local', 'desc_tipo_acceso_local','id_situacion_local', 'desc_situacion_local', 'clase_vial_edificio', 'desc_vial_edificio', 'id_ndp_edificio','id_clase_ndp_edificio', 'nom_edificio','num_edificio','cal_edificio', 'secuencial_local_PC', 'id_vial_acceso', 'clase_vial_acceso', 'desc_vial_acceso', 'id_ndp_acceso', 'id_clase_ndp_acceso', 'nom_acceso','num_acceso','coordenada_x_agrupacion', 'coordenada_y_agrup','id_agrupacion', 'id_planta_agrupado', 'id_local_agrupado', 'cal_acceso','rotulo'

Tras limpiar columnas, haré un merge con df_locales19 como base completando con variables de df_epi19. Total: 163317 x 36 variables

In [300]:
df_local19_clean.columns

Index(['id_local', 'id_vial_edificio', 'coordenada_x_agrupacion_x',
       'coordenada_y_agrup_x', 'id_agrupacion', 'nombre_agrupacion',
       'id_tipo_agrup', 'desc_tipo_agrup', 'id_planta_agrupado',
       'id_local_agrupado', 'id_seccion', 'desc_seccion', 'id_division',
       'desc_division', 'id_epigrafe', 'desc_epigrafe', 'id_distrito_local',
       'desc_distrito_local', 'id_barrio_local', 'desc_barrio_local',
       'desc_seccion_censal_local', 'coordenada_x_local', 'coordenada_y_local',
       'desc_tipo_acceso_local', 'id_situacion_local', 'desc_situacion_local',
       'clase_vial_edificio', 'desc_vial_edificio', 'id_ndp_edificio',
       'id_clase_ndp_edificio', 'nom_edificio', 'num_edificio', 'cal_edificio',
       'secuencial_local_PC', 'clase_vial_acceso', 'desc_vial_acceso',
       'id_ndp_acceso', 'id_clase_ndp_acceso', 'nom_acceso', 'num_acceso',
       'coordenada_x_agrupacion_y', 'coordenada_y_agrup_y', 'rotulo'],
      dtype='object')

In [443]:
#Drop columns que no interesan
df_local19_d = df_locales19.drop(['cod_barrio_local', 'id_seccion_censal_local', 'id_tipo_acceso_local', 'id_vial_acceso', 
                               'id_vial_edificio', 'coordenada_x_agrupacion', 'coordenada_y_agrup',
                                  'id_agrupacion','nombre_agrupacion', 
                               'id_tipo_agrup', 'desc_tipo_agrup', 'id_planta_agrupado', 
                               'id_local_agrupado', 'cal_acceso'], axis  = 1)

df_epi19_d = df_epi19.drop(['id_distrito_local', 'desc_distrito_local', 'id_barrio_local', 
                            'desc_barrio_local', 'cod_barrio_local','id_seccion_censal_local',
                            'desc_seccion_censal_local', 
                            'coordenada_x_local', 'coordenada_y_local', 
                            'id_tipo_acceso_local', 'desc_tipo_acceso_local', 
                            'id_situacion_local', 'desc_situacion_local', 
                            'clase_vial_edificio', 'desc_vial_edificio', 'id_ndp_edificio',
                            'id_clase_ndp_edificio', 'nom_edificio', 'num_edificio', 
                            'cal_edificio', 'secuencial_local_PC', 
                            'id_vial_acceso', 'clase_vial_acceso', 'desc_vial_acceso', 
                            'id_ndp_acceso', 'id_clase_ndp_acceso', 'nom_acceso', 
                            'num_acceso', 'coordenada_x_agrupacion', 'coordenada_y_agrup',
                            'id_agrupacion', 'id_planta_agrupado', 'id_local_agrupado',
                            'cal_acceso','rotulo'], axis  = 1)

In [444]:
df_local19_d.shape, df_epi19_d.shape

((147318, 26), (163316, 11))

In [445]:
df_local19_clean = df_local19_d.merge(df_epi19_d, how= 'outer', on=['id_local'])

In [446]:
df_local19_clean.shape

(163317, 36)

In [305]:
df_local19_clean.columns

Index(['id_local', 'id_distrito_local', 'desc_distrito_local',
       'id_barrio_local', 'desc_barrio_local', 'desc_seccion_censal_local',
       'coordenada_x_local', 'coordenada_y_local', 'desc_tipo_acceso_local',
       'id_situacion_local', 'desc_situacion_local', 'clase_vial_edificio',
       'desc_vial_edificio', 'id_ndp_edificio', 'id_clase_ndp_edificio',
       'nom_edificio', 'num_edificio', 'cal_edificio', 'secuencial_local_PC',
       'clase_vial_acceso', 'desc_vial_acceso', 'id_ndp_acceso',
       'id_clase_ndp_acceso', 'nom_acceso', 'num_acceso', 'rotulo',
       'id_vial_edificio', 'coordenada_x_agrupacion', 'coordenada_y_agrup',
       'id_agrupacion', 'nombre_agrupacion', 'id_tipo_agrup',
       'desc_tipo_agrup', 'id_planta_agrupado', 'id_local_agrupado',
       'id_seccion', 'desc_seccion', 'id_division', 'desc_division',
       'id_epigrafe', 'desc_epigrafe'],
      dtype='object')

In [447]:
df_local19_clean.head()

id_local  id_distrito_local   desc_distrito_local  id_barrio_local  \
0  280018574                  2  ARGANZUELA                        204   
1  280018581                  2  ARGANZUELA                        202   
2  280018581                  2  ARGANZUELA                        202   
3  280018584                  2  ARGANZUELA                        202   
4  280018586                  2  ARGANZUELA                        206   

      desc_barrio_local  desc_seccion_censal_local coordenada_x_local  \
0  LEGAZPI                                     103          442298,57   
1  ACACIAS                                      20          440053,59   
2  ACACIAS                                      20          440053,59   
3  ACACIAS                                      20          440069,59   
4  PALOS DE MOGUER                              80          441058,58   

  coordenada_y_local desc_tipo_acceso_local  id_situacion_local  \
0         4471790,51           Puerta Calle                   1   
1         4473007,53           Puerta Calle                   1   
2         4473007,53           Puerta Calle                   1   
3         4472915,53           Puerta Calle                   1   
4         4473091,52           Puerta Calle                   1   

  desc_situacion_local       clase_vial_edificio  \
0              Abierto  AVENIDA                    
1              Abierto  RONDA                      
2              Abierto  RONDA                      
3              Abierto  RONDA                      
4              Abierto  PASEO                      

                                  desc_vial_edificio  id_ndp_edificio  \
0  PLANETARIO                                    ...         20141783   
1  TOLEDO                                        ...         20147610   
2  TOLEDO                                        ...         20147610   
3  TOLEDO                                        ...         20147610   
4  SANTA MARIA DE LA CABEZA                      ...         20149322   

   id_clase_ndp_edificio nom_edificio  num_edificio cal_edificio  \
0                      1          NUM             1            A   
1                      1          NUM            20            A   
2                      1          NUM            20            A   
3                      1          NUM            20            A   
4                      1          NUM            12                

   secuencial_local_PC         clase_vial_acceso  \
0                   10  AVENIDA                    
1                   10  RONDA                      
2                   10  RONDA                      
3                   70  CALLE                      
4                   30  PASEO                      

                                    desc_vial_acceso  id_ndp_acceso  \
0  PLANETARIO                                    ...       20141783   
1  TOLEDO                                        ...       20147610   
2  TOLEDO                                        ...       20147610   
3  VILLA DE ARBANCON                             ...       20121546   
4  SANTA MARIA DE LA CABEZA                      ...       20149322   

   id_clase_ndp_acceso nom_acceso  num_acceso         rotulo  \
0                    1        NUM           1            FCC   
1                    1        NUM          20          GYATA   
2                    1        NUM          20          GYATA   
3                    1        NUM           4      MERCADONA   
4                    1        NUM          12  FAMILIA UNIDA   

   id_vial_edificio nombre_agrupacion  id_tipo_agrup desc_tipo_agrup  \
0             831.0               NaN            NaN             NaN   
1          743800.0               NaN            NaN             NaN   
2          743800.0               NaN            NaN             NaN   
3          743800.0               NaN            NaN             NaN   
4          697200.0               NaN            NaN             NaN   

Compruebo nulos y tratamos missing values

In [448]:
df_local19_clean.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 163317 entries, 0 to 163316
Data columns (total 36 columns):
id_local                     163317 non-null int64
id_distrito_local            163317 non-null int64
desc_distrito_local          163317 non-null object
id_barrio_local              163317 non-null int64
desc_barrio_local            163317 non-null object
desc_seccion_censal_local    163317 non-null int64
coordenada_x_local           163317 non-null object
coordenada_y_local           163317 non-null object
desc_tipo_acceso_local       163317 non-null object
id_situacion_local           163317 non-null int64
desc_situacion_local         163317 non-null object
clase_vial_edificio          163317 non-null object
desc_vial_edificio           163317 non-null object
id_ndp_edificio              163317 non-null int64
id_clase_ndp_edificio        163317 non-null int64
nom_edificio                 163317 non-null object
num_edificio                 163317 non-null int64
cal_edificio 

El principal campo para saber el tipo de local es 'desc_epigrafe' o 'id_epigrafe' y ahy un 40k nulls.   
Reviso los nulos. Aunque antes completo con el 'CAÑAS y TAPAS' que por error no estaba en el fichero de Epigrafes

In [449]:
df_local19_clean[df_local19_clean['rotulo'] == 'CAÑAS Y TAPAS']

id_local  id_distrito_local   desc_distrito_local  id_barrio_local  \
56137   10003543                  1  CENTRO                            101   
56428   30000501                  3  RETIRO                            303   
59960   80001076                  8  FUENCARRAL-EL PARDO               804   
76868  270375122                  1  CENTRO                            101   
81052  270419395                  1  CENTRO                            102   
82172  270456853                  1  CENTRO                            106   

          desc_barrio_local  desc_seccion_censal_local coordenada_x_local  \
56137  PALACIO                                      11          439691,59   
56428  ESTRELLA                                     42                  0   
59960  EL PILAR                                     45          440241,62   
76868  PALACIO                                       2           439714,6   
81052  EMBAJADORES                                  58          441209,58   
82172  SOL                                         124          440099,59   

      coordenada_y_local desc_tipo_acceso_local  id_situacion_local  \
56137         4473697,53           Puerta Calle                   1   
56428                  0           Puerta Calle                   9   
59960         4481242,55               Agrupado                   1   
76868         4474953,54           Puerta Calle                   1   
81052         4473384,52           Puerta Calle                   1   
82172         4474326,53           Puerta Calle                   1   

      desc_situacion_local       clase_vial_edificio  \
56137              Abierto  PLAZA                      
56428   Baja Reunificacion  CALLE                      
59960              Abierto  AVENIDA                    
76868              Abierto  CALLE                      
81052              Abierto  CALLE                      
82172              Abierto  PLAZA                      

                                      desc_vial_edificio  id_ndp_edificio  \
56137  PUERTA DE MOROS                               ...         11000722   
56428  VALORES                                       ...         11012021   
59960  MONFORTE DE LEMOS                             ...         20095319   
76868  GRAN VIA                                      ...         11000111   
81052  DOCTOR DRUMEN                                 ...         11003118   
82172  CELENQUE                                      ...         11007853   

       id_clase_ndp_edificio nom_edificio  num_edificio cal_edificio  \
56137                      1          NUM             8                
56428                      1          NUM             1                
59960                      1          NUM            30                
76868                      1          NUM            71                
81052                      1          NUM             3                
82172                      1          NUM             1                

       secuencial_local_PC         clase_vial_acceso  \
56137                   20  PLAZA                      
56428                   20  CALLE                      
59960                    0  AVENIDA                    
76868                   20  CALLE                      
81052                   10  CALLE                      
82172                   30  PLAZA                      

                                        desc_vial_acceso  id_ndp_acceso  \
56137  HUMILLADERO                                   ...       31041413   
56428  VALORES                                       ...       11012021   
59960  MONFORTE DE LEMOS                             ...       31049013   
76868  GRAN VIA                                      ...       11000111   
81052  DOCTOR DRUMEN                                 ...       11003118   
82172  CELENQUE                                      ...       11007853   

       id_clase_ndp_acceso nom_acceso  num_acceso         rotulo  

In [450]:
df_local19_clean[df_local19_clean['id_local'] == 10003543]

id_local  id_distrito_local   desc_distrito_local  id_barrio_local  \
56137  10003543                  1  CENTRO                            101   

          desc_barrio_local  desc_seccion_censal_local coordenada_x_local  \
56137  PALACIO                                      11          439691,59   

      coordenada_y_local desc_tipo_acceso_local  id_situacion_local  \
56137         4473697,53           Puerta Calle                   1   

      desc_situacion_local       clase_vial_edificio  \
56137              Abierto  PLAZA                      

                                      desc_vial_edificio  id_ndp_edificio  \
56137  PUERTA DE MOROS                               ...         11000722   

       id_clase_ndp_edificio nom_edificio  num_edificio cal_edificio  \
56137                      1          NUM             8                

       secuencial_local_PC         clase_vial_acceso  \
56137                   20  PLAZA                      

                                        desc_vial_acceso  id_ndp_acceso  \
56137  HUMILLADERO                                   ...       31041413   

       id_clase_ndp_acceso nom_acceso  num_acceso         rotulo  \
56137                    1        NUM           5  CAÑAS Y TAPAS   

       id_vial_edificio nombre_agrupacion  id_tipo_agrup desc_tipo_agrup  \
56137          614800.0               NaN            NaN             NaN   

      id_seccion desc_seccion id_division                   desc_division  \
56137          I   HOSTELERIA          56  SERVICIOS DE COMIDAS Y BEBIDAS   

      id_epigrafe    desc_epigrafe  
56137      561004  BAR RESTAURANTE

In [451]:
df_local19_clean[df_local19_clean['id_local'] == 80001076]

id_local  id_distrito_local   desc_distrito_local  id_barrio_local  \
59960  80001076                  8  FUENCARRAL-EL PARDO               804   

          desc_barrio_local  desc_seccion_censal_local coordenada_x_local  \
59960  EL PILAR                                     45          440241,62   

      coordenada_y_local desc_tipo_acceso_local  id_situacion_local  \
59960         4481242,55               Agrupado                   1   

      desc_situacion_local       clase_vial_edificio  \
59960              Abierto  AVENIDA                    

                                      desc_vial_edificio  id_ndp_edificio  \
59960  MONFORTE DE LEMOS                             ...         20095319   

       id_clase_ndp_edificio nom_edificio  num_edificio cal_edificio  \
59960                      1          NUM            30                

       secuencial_local_PC         clase_vial_acceso  \
59960                    0  AVENIDA                    

                                        desc_vial_acceso  id_ndp_acceso  \
59960  MONFORTE DE LEMOS                             ...       31049013   

       id_clase_ndp_acceso nom_acceso  num_acceso         rotulo  \
59960                    1        NUM          36  CAÑAS Y TAPAS   

       id_vial_edificio nombre_agrupacion  id_tipo_agrup desc_tipo_agrup  \
59960               NaN               NaN            NaN             NaN   

      id_seccion desc_seccion id_division desc_division id_epigrafe  \
59960        NaN          NaN         NaN           NaN         NaN   

      desc_epigrafe  
59960           NaN

In [452]:
df_locales19[df_locales19['id_local'] == 80001076]

id_local  id_distrito_local   desc_distrito_local  id_barrio_local  \
54437  80001076                  8  FUENCARRAL-EL PARDO               804   

          desc_barrio_local  cod_barrio_local  id_seccion_censal_local  \
54437  EL PILAR                           NaN                      NaN   

       desc_seccion_censal_local coordenada_x_local coordenada_y_local  \
54437                         45          440241,62         4481242,55   

       id_tipo_acceso_local desc_tipo_acceso_local  id_situacion_local  \
54437                   NaN               Agrupado                   1   

      desc_situacion_local  id_vial_edificio       clase_vial_edificio  \
54437              Abierto               NaN  AVENIDA                    

                                      desc_vial_edificio  id_ndp_edificio  \
54437  MONFORTE DE LEMOS                             ...         20095319   

       id_clase_ndp_edificio nom_edificio  num_edificio cal_edificio  \
54437                      1          NUM            30                

       secuencial_local_PC  id_vial_acceso         clase_vial_acceso  \
54437                    0             NaN  AVENIDA                    

                                        desc_vial_acceso  id_ndp_acceso  \
54437  MONFORTE DE LEMOS                             ...       31049013   

       id_clase_ndp_acceso nom_acceso  num_acceso cal_acceso  \
54437                    1        NUM          36              

      coordenada_x_agrupacion coordenada_y_agrup  id_agrupacion  \
54437               440241,62         4481242,55     99000109.0   

                 nombre_agrupacion  id_tipo_agrup   desc_tipo_agrup  \
54437  CENTRO COMERCIAL LA VAGUADA            1.0  Centro Comercial   

      id_planta_agrupado id_local_agrupado         rotulo  
54437                  2                23  CAÑAS Y TAPAS

In [453]:
df_local19_clean.loc[59960,['nombre_agrupacion','id_tipo_agrup',
                            'desc_tipo_agrup','id_seccion','desc_seccion','id_division',
                            'desc_division','id_epigrafe','desc_epigrafe']] = ['CENTRO COMERCIAL LA VAGUADA','1.0','Centro Comercial','I','HOSTELERIA','56','SERVICIOS DE COMIDAS Y BEBIDAS','561004','BAR RESTAURANTE']

In [454]:
df_local19_clean[df_local19_clean['id_local'] == 80001076]

id_local  id_distrito_local   desc_distrito_local  id_barrio_local  \
59960  80001076                  8  FUENCARRAL-EL PARDO               804   

          desc_barrio_local  desc_seccion_censal_local coordenada_x_local  \
59960  EL PILAR                                     45          440241,62   

      coordenada_y_local desc_tipo_acceso_local  id_situacion_local  \
59960         4481242,55               Agrupado                   1   

      desc_situacion_local       clase_vial_edificio  \
59960              Abierto  AVENIDA                    

                                      desc_vial_edificio  id_ndp_edificio  \
59960  MONFORTE DE LEMOS                             ...         20095319   

       id_clase_ndp_edificio nom_edificio  num_edificio cal_edificio  \
59960                      1          NUM            30                

       secuencial_local_PC         clase_vial_acceso  \
59960                    0  AVENIDA                    

                                        desc_vial_acceso  id_ndp_acceso  \
59960  MONFORTE DE LEMOS                             ...       31049013   

       id_clase_ndp_acceso nom_acceso  num_acceso         rotulo  \
59960                    1        NUM          36  CAÑAS Y TAPAS   

       id_vial_edificio            nombre_agrupacion id_tipo_agrup  \
59960               NaN  CENTRO COMERCIAL LA VAGUADA           1.0   

        desc_tipo_agrup id_seccion desc_seccion id_division  \
59960  Centro Comercial          I   HOSTELERIA          56   

                        desc_division id_epigrafe    desc_epigrafe  
59960  SERVICIOS DE COMIDAS Y BEBIDAS      561004  BAR RESTAURANTE

In [455]:
df_local19_clean[df_local19_clean['desc_epigrafe'].isnull()]

id_local  id_distrito_local   desc_distrito_local  id_barrio_local  \
5       280018588                  2  ARGANZUELA                        201   
84      280019727                  3  RETIRO                            301   
146     280020051                  3  RETIRO                            302   
148     280020056                  3  RETIRO                            302   
149     280020058                  3  RETIRO                            302   
174     280020163                  3  RETIRO                            303   
240     280020519                  3  RETIRO                            305   
258     280020589                  3  RETIRO                            305   
259     280020591                  3  RETIRO                            305   
394     280021252                  5  CHAMARTIN                         501   
400     280021282                  5  CHAMARTIN                         501   
412     280021334                  5  CHAMARTIN                         502   
522     280021841                  5  CHAMARTIN                         502   
531     280021855                  5  CHAMARTIN                         502   
568     280022039                  5  CHAMARTIN                         503   
584     280022099                  5  CHAMARTIN                         503   
593     280022141                  5  CHAMARTIN                         503   
594     280022147                  5  CHAMARTIN                         503   
633     280022345                  5  CHAMARTIN                         504   
662     280022485                  5  CHAMARTIN                         504   
694     280022620                  5  CHAMARTIN                         504   
697     280022626                  5  CHAMARTIN                         504   
748     280022835                  5  CHAMARTIN                         505   
776     280022938                  5  CHAMARTIN                         505   
808     280023079                  5  CHAMARTIN                         506   
884     280023433                  5  CHAMARTIN                         504   
943     280023717                 21  BARAJAS                          2103   
990     280023954                 21  BARAJAS                          2105   
1016    280024069                 21  BARAJAS                          2101   
1020    280024179                  3  RETIRO                            302   
...           ...                ...                   ...              ...   
162895  285047307                 15  CIUDAD LINEAL                    1502   
162896  285047308                 15  CIUDAD LINEAL                    1502   
162897  285047310                 15  CIUDAD LINEAL                    1502   
162898  285047313                 15  CIUDAD LINEAL                    1502   
162899  285047328                 15  CIUDAD LINEAL                    1503   
162900  285047329                 15  CIUDAD LINEAL                    1503   
162901  285047330                 15  CIUDAD LINEAL                    1503   
162902  285047332                 15  CIUDAD LINEAL                    1503   
162903  285047334                 15  CIUDAD LINEAL                    1503   
162904  285047337                 15  CIUDAD LINEAL                    1503   
162905  285047341                 15  CIUDAD LINEAL                    1506   
162906  285047356                 15  CIUDAD LINEAL                    1501   
162908  285047377                 15  CIUDAD LINEAL                    1502   
162909  285047378                 15  CIUDAD LINEAL                    1502   
162924  290000036                  4  SALAMANCA                         403   
162929  290000050                  4  SALAMANCA                         405   
162940  290000122                  4  SALAMANCA                         403   
162941  290000126                  4  SALAMANCA                         404   
162943  290000134                  4  SALAMANCA            

Los nulos corresponden a locales sin actividad (según se indica en la variable rotulo).   
Los eliminamos.
Nota: posteriormente vi que existen desc_epigrafes = LOCAL SIN ACTIVIDAD. 
En vez de eliminarlos los voy a fillna con los valores de los epigrafes sin actividad. Además he visto que en muchos casos, el estado de "desc_situacion_local" es Abierto.
Con esto, crearé una variable estado que modifique es estado de Abierto a Cerrado cuando la "desc_epigrafe" indique que es un local sin Actividad. Aprovecharé para unificar también la baja de local en Cerrado. Ya se indicaba en los documentos que explican las variables que el campo 'desc_situacion_local' es muy complicado de mantener actualizado.


In [456]:
#df_local19_clean.dropna(subset=['desc_epigrafe'], inplace=True)
df_local19_clean['id_seccion'].fillna('Z',inplace=True)
df_local19_clean['desc_seccion'].fillna('SIN ACTIVIDAD',inplace=True)
df_local19_clean['id_division'].fillna(0,inplace=True)
df_local19_clean['desc_division'].fillna('SIN ACTIVIDAD',inplace=True)
df_local19_clean['id_epigrafe'].fillna(0,inplace=True)
df_local19_clean['desc_epigrafe'].fillna('LOCAL SIN ACTIVIDAD',inplace=True)
df_local19_clean.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 163317 entries, 0 to 163316
Data columns (total 36 columns):
id_local                     163317 non-null int64
id_distrito_local            163317 non-null int64
desc_distrito_local          163317 non-null object
id_barrio_local              163317 non-null int64
desc_barrio_local            163317 non-null object
desc_seccion_censal_local    163317 non-null int64
coordenada_x_local           163317 non-null object
coordenada_y_local           163317 non-null object
desc_tipo_acceso_local       163317 non-null object
id_situacion_local           163317 non-null int64
desc_situacion_local         163317 non-null object
clase_vial_edificio          163317 non-null object
desc_vial_edificio           163317 non-null object
id_ndp_edificio              163317 non-null int64
id_clase_ndp_edificio        163317 non-null int64
nom_edificio                 163317 non-null object
num_edificio                 163317 non-null int64
cal_edificio 

Ahora trato los NaN de locales agregados completando con valores de que no son agrupación

In [457]:
df_local19_clean['nombre_agrupacion'].fillna('SIN AGRUPACION',inplace=True)
df_local19_clean['desc_tipo_agrup'].fillna('SIN AGRUPACION',inplace=True)
df_local19_clean['id_tipo_agrup'].fillna(-1,inplace=True)

Revisión final de que todo está correcto

In [458]:
df_local19_clean.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 163317 entries, 0 to 163316
Data columns (total 36 columns):
id_local                     163317 non-null int64
id_distrito_local            163317 non-null int64
desc_distrito_local          163317 non-null object
id_barrio_local              163317 non-null int64
desc_barrio_local            163317 non-null object
desc_seccion_censal_local    163317 non-null int64
coordenada_x_local           163317 non-null object
coordenada_y_local           163317 non-null object
desc_tipo_acceso_local       163317 non-null object
id_situacion_local           163317 non-null int64
desc_situacion_local         163317 non-null object
clase_vial_edificio          163317 non-null object
desc_vial_edificio           163317 non-null object
id_ndp_edificio              163317 non-null int64
id_clase_ndp_edificio        163317 non-null int64
nom_edificio                 163317 non-null object
num_edificio                 163317 non-null int64
cal_edificio 

Comprobamos homogeneidad en los tipos dentro den cada variable

In [459]:
df_epi19.dtypes

id_local                       int64
id_distrito_local              int64
desc_distrito_local           object
id_barrio_local                int64
desc_barrio_local             object
cod_barrio_local             float64
id_seccion_censal_local      float64
desc_seccion_censal_local      int64
coordenada_x_local            object
coordenada_y_local            object
id_tipo_acceso_local         float64
desc_tipo_acceso_local        object
id_situacion_local           float64
desc_situacion_local          object
id_vial_edificio               int64
clase_vial_edificio           object
desc_vial_edificio            object
id_ndp_edificio                int64
id_clase_ndp_edificio          int64
nom_edificio                  object
num_edificio                   int64
cal_edificio                  object
secuencial_local_PC            int64
id_vial_acceso               float64
clase_vial_acceso             object
desc_vial_acceso              object
id_ndp_acceso                  int64
i

In [460]:
df_local19_clean.dtypes 
#a priori lo único que no encaja es id_tipo_agrup. Lo hacemos numerico

id_local                       int64
id_distrito_local              int64
desc_distrito_local           object
id_barrio_local                int64
desc_barrio_local             object
desc_seccion_censal_local      int64
coordenada_x_local            object
coordenada_y_local            object
desc_tipo_acceso_local        object
id_situacion_local             int64
desc_situacion_local          object
clase_vial_edificio           object
desc_vial_edificio            object
id_ndp_edificio                int64
id_clase_ndp_edificio          int64
nom_edificio                  object
num_edificio                   int64
cal_edificio                  object
secuencial_local_PC            int64
clase_vial_acceso             object
desc_vial_acceso              object
id_ndp_acceso                  int64
id_clase_ndp_acceso            int64
nom_acceso                    object
num_acceso                     int64
rotulo                        object
id_vial_edificio             float64
n

In [461]:
#cambiamos id_tipo_agrup a numérico
df_local19_clean['id_tipo_agrup'] = df_local19_clean['id_tipo_agrup'].apply(pd.to_numeric)

Ya tengo el tablón de 2019 limpio y preparado para añadir el resto de años

In [434]:
#muy pocos cerrados o de baja en 2019. Voy a revisar situaciones como
#desc_epigrafe LOCAL SIN ACTIVIDAD
df_local19_clean.groupby('desc_situacion_local').count()

id_local  id_distrito_local  desc_distrito_local  \
desc_situacion_local                                                     
Abierto                 115941             115941               115941   
Baja                       372                372                  372   
Baja PC Asociado             9                  9                    9   
Baja Reunificacion        1464               1464                 1464   
Cerrado                   3943               3943                 3943   
En obras                    95                 95                   95   
Uso vivienda                66                 66                   66   

                      id_barrio_local  desc_barrio_local  \
desc_situacion_local                                       
Abierto                        115941             115941   
Baja                              372                372   
Baja PC Asociado                    9                  9   
Baja Reunificacion               1464               1464   
Cerrado                          3943               3943   
En obras                           95                 95   
Uso vivienda                       66                 66   

                      desc_seccion_censal_local  coordenada_x_local  \
desc_situacion_local                                                  
Abierto                                  115941              115941   
Baja                                        372                 372   
Baja PC Asociado                              9                   9   
Baja Reunificacion                         1464                1464   
Cerrado                                    3943                3943   
En obras                                     95                  95   
Uso vivienda                                 66                  66   

                      coordenada_y_local  desc_tipo_acceso_local  \
desc_situacion_local                                               
Abierto                           115941                  115941   
Baja                                 372                     372   
Baja PC Asociado                       9                       9   
Baja Reunificacion                  1464                    1464   
Cerrado                             3943                    3943   
En obras                              95                      95   
Uso vivienda                          66                      66   

                      id_situacion_local  clase_vial_edificio  \
desc_situacion_local                                            
Abierto                           115941               115941   
Baja                                 372                  372   
Baja PC Asociado                       9                    9   
Baja Reunificacion                  1464                 1464   
Cerrado                             3943                 3943   
En obras                              95                   95   
Uso vivienda                          66                   66   

                      desc_vial_edificio  id_ndp_edificio  \
desc_situacion_local                                        
Abierto                           115941           115941   
Baja                                 372              372   
Baja PC Asociado                       9                9   
Baja Reunificacion                  1464             1464   
Cerrado                             3943             3943   
En obras                              95               95   
Uso vivienda                          66               66   

                      id_clase_ndp_edificio  nom_edificio  num_edificio  \
desc_situacion_local                                                      
Abierto                              115941        115941        115941   
Baja                                    372           372           372   
Baja PC Asociado                          9             9             9   
Baja Reunificacion                     1464       

In [474]:
#muy pocos cerrados o de baja en 2019. Voy a revisar situaciones como
#desc_epigrafe LOCAL SIN ACTIVIDAD
cerr = df_local19_clean[df_local19_clean['desc_epigrafe'] == 'LOCAL SIN ACTIVIDAD'] 
cerr.groupby('desc_situacion_local').count()

id_local  id_distrito_local  desc_distrito_local  \
desc_situacion_local                                                     
Abierto                   2870               2870                 2870   
Baja                       650                650                  650   
Baja PC Asociado             2                  2                    2   
Baja Reunificacion         983                983                  983   
Cerrado                  31118              31118                31118   
En obras                   748                748                  748   
Uso vivienda              6436               6436                 6436   

                      id_barrio_local  desc_barrio_local  \
desc_situacion_local                                       
Abierto                          2870               2870   
Baja                              650                650   
Baja PC Asociado                    2                  2   
Baja Reunificacion                983                983   
Cerrado                         31118              31118   
En obras                          748                748   
Uso vivienda                     6436               6436   

                      desc_seccion_censal_local  coordenada_x_local  \
desc_situacion_local                                                  
Abierto                                    2870                2870   
Baja                                        650                 650   
Baja PC Asociado                              2                   2   
Baja Reunificacion                          983                 983   
Cerrado                                   31118               31118   
En obras                                    748                 748   
Uso vivienda                               6436                6436   

                      coordenada_y_local  desc_tipo_acceso_local  \
desc_situacion_local                                               
Abierto                             2870                    2870   
Baja                                 650                     650   
Baja PC Asociado                       2                       2   
Baja Reunificacion                   983                     983   
Cerrado                            31118                   31118   
En obras                             748                     748   
Uso vivienda                        6436                    6436   

                      id_situacion_local  clase_vial_edificio  \
desc_situacion_local                                            
Abierto                             2870                 2870   
Baja                                 650                  650   
Baja PC Asociado                       2                    2   
Baja Reunificacion                   983                  983   
Cerrado                            31118                31118   
En obras                             748                  748   
Uso vivienda                        6436                 6436   

                      desc_vial_edificio  id_ndp_edificio  \
desc_situacion_local                                        
Abierto                             2870             2870   
Baja                                 650              650   
Baja PC Asociado                       2                2   
Baja Reunificacion                   983              983   
Cerrado                            31118            31118   
En obras                             748              748   
Uso vivienda                        6436             6436   

                      id_clase_ndp_edificio  nom_edificio  num_edificio  \
desc_situacion_local                                                      
Abierto                                2870          2870          2870   
Baja                                    650           650           650   
Baja PC Asociado                          2             2             2   
Baja Reunificacion                      983       

In [480]:
#Prueba a borrar
df_local19_clean[(df_local19_clean['desc_epigrafe'] == 'LOCAL SIN ACTIVIDAD')
                & (df_local19_clean['desc_situacion_local'] == 'Abierto')].count()

id_local                     2870
id_distrito_local            2870
desc_distrito_local          2870
id_barrio_local              2870
desc_barrio_local            2870
desc_seccion_censal_local    2870
coordenada_x_local           2870
coordenada_y_local           2870
desc_tipo_acceso_local       2870
id_situacion_local           2870
desc_situacion_local         2870
clase_vial_edificio          2870
desc_vial_edificio           2870
id_ndp_edificio              2870
id_clase_ndp_edificio        2870
nom_edificio                 2870
num_edificio                 2870
cal_edificio                 2870
secuencial_local_PC          2870
clase_vial_acceso            2870
desc_vial_acceso             2870
id_ndp_acceso                2870
id_clase_ndp_acceso          2870
nom_acceso                   2870
num_acceso                   2870
rotulo                       2870
id_vial_edificio             2870
nombre_agrupacion            2870
id_tipo_agrup                2870
desc_tipo_agru

# REVISAR DESDE AQUI 

In [441]:
sin_act = df_local19_clean[df_local19_clean['desc_epigrafe']=='LOCAL SIN ACTIVIDAD']
sin_act.head()

id_local  id_distrito_local   desc_distrito_local  id_barrio_local  \
7    280018593                  2  ARGANZUELA                        204   
438  280021465                  5  CHAMARTIN                         502   
451  280021522                  5  CHAMARTIN                         502   
529  280021853                  5  CHAMARTIN                         502   
579  280022087                  5  CHAMARTIN                         504   

        desc_barrio_local  desc_seccion_censal_local coordenada_x_local  \
7    LEGAZPI                                     100          441166,58   
438  PROSPERIDAD                                  21          443268,59   
451  PROSPERIDAD                                  24          443423,58   
529  PROSPERIDAD                                  99          443722,58   
579  HISPANOAMERICA                               53          443524,59   

    coordenada_y_local desc_tipo_acceso_local  id_situacion_local  \
7           4471267,52           Puerta Calle                   1   
438          4477529,5           Puerta Calle                   4   
451          4477434,5           Puerta Calle                   4   
529         4477699,49           Puerta Calle                   1   
579          4478315,5           Puerta Calle                   1   

    desc_situacion_local       clase_vial_edificio  \
7                Abierto  CALLE                      
438              Cerrado  CALLE                      
451              Cerrado  CALLE                      
529              Abierto  CALLE                      
579              Abierto  CALLE                      

                                    desc_vial_edificio  id_ndp_edificio  \
7    FRIGILIANA                                    ...         20155774   
438  RAMOS CARRION                                 ...         11022264   
451  CORAZON DE MARIA                              ...         11022341   
529  MARTIN MACHIO                                 ...         11022966   
579  CELINDAS                                      ...         11024700   

     id_clase_ndp_edificio nom_edificio  num_edificio cal_edificio  \
7                        1          NUM             2            A   
438                      1          NUM             6                
451                      1          NUM            43                
529                      1          NUM             8                
579                      1          NUM            13                

     secuencial_local_PC         clase_vial_acceso  \
7                     10  PASEO                      
438                   10  CALLE                      
451                   10  CALLE                      
529                   20  CALLE                      
579                   10  CALLE                      

                                      desc_vial_acceso  id_ndp_acceso  \
7    MOLINO                                        ...       31051276   
438  RAMOS CARRION                                 ...       11022264   
451  CORAZON DE MARIA                              ...       11022341   
529  MARTIN MACHIO                                 ...       11022966   
579  CELINDAS                                      ...       11024700   

     id_clase_ndp_acceso nom_acceso  num_acceso  \
7                      1        NUM           6   
438                    1        NUM           6   
451                    1        NUM          43   
529                    1        NUM           8   
579                    1        NUM          13   

                                   rotulo  id_vial_edificio nombre_agrupacion  \
7                        VIENA CAPELLANES            2918.0    SIN AGRUPACION   
438                             MAMA CUCA          631400.0    SIN AGRUPACION   
451                           MAS COMPANY          210200.0    SIN AGRUPACION   
529                                    SR          489800.0    SIN AGRUPACION   
579  ASOCI

In [ ]:
Sin_actividad = df_local19_clean['desc_epigrafe']=='LOCAL SIN ACTIVIDAD'
Abierto = df_local19_clean['desc_situacion_local'
df_local19_clean[Sin_actividad & Abierto]

Decido volver atrásRetomar los NaN que borre que desc_epigrafe y ponerlos como sin actividad.
Ver cuantos estan en estado abierto y crear una nueva variable que sea
estado donde corrija los que aparecen abiertos y realmente están
sin actividad

In [432]:
df_local19_clean.groupby(['desc_situacion_local','id_distrito_local',
                          'desc_epigrafe']).count()

id_local  \
desc_situacion_local id_distrito_local desc_epigrafe                                                  
Abierto              1                 ACABADO DE EDIFICIOS (CARPINTERIA, REVOCAMIENTO...        12   
                                       ACTIVIDADES ADMINISTRATIVAS Y AUXILIARES DE OFI...       158   
                                       ACTIVIDADES ANEXAS AL TRANSPORTE                          12   
                                       ACTIVIDADES AUXILIARES A SEGUROS Y FONDOS DE PE...         4   
                                       ACTIVIDADES CINEMATOGRAFICAS, DE VIDEO Y DE TEL...        18   
                                       ACTIVIDADES DE APOYO A LAS EMPRESAS N.C.O.P. (A...         2   
                                       ACTIVIDADES DE BIBLIOTECAS, ARCHIVOS, MUSEOS Y ...        35   
                                       ACTIVIDADES DE CLUBES DEPORTIVOS Y OTRAS ACTIVI...         2   
                                       ACTIVIDADES DE CONSULTORIA DE GESTION EMPRESARIAL          5   
                                       ACTIVIDADES DE CONTABILIDAD, TENEDURIA, AUDITOR...        18   
                                       ACTIVIDADES DE CREACION, ARTISTICAS Y ESPECTACULOS        50   
                                       ACTIVIDADES DE DISEÑO ESPECIALIZADO                       24   
                                       ACTIVIDADES DE GESTION DE FONDOS                           1   
                                       ACTIVIDADES DE GRABACION DE SONIDO Y EDICION MU...         4   
                                       ACTIVIDADES DE LAS AGENCIAS DE COLOCACION                  1   
                                       ACTIVIDADES DE LAS EMPRESAS DE TRABAJO TEMPORAL            1   
                                       ACTIVIDADES DE LAS SEDES CENTRALES                        10   
                                       ACTIVIDADES DE LIMPIEZA                                    8   
                                       ACTIVIDADES DE LOS GIMNASIOS                              40   
                                       ACTIVIDADES DE ORGANIZACIONES POLITICAS                    6   
                                       ACTIVIDADES DE ORGANIZACIONES RELIGIOSAS                  74   
                                       ACTIVIDADES DE ORGANIZACIONES Y ORGANISMOS EXTR...         2   
                                       ACTIVIDADES DE PROGRAMACION Y EMISION DE RADIO ...         2   
                                       ACTIVIDADES DE SEGURIDAD PRIVADA                           1   
                                       ACTIVIDADES DE SERVICIOS SOCIALES SIN ALOJAMIEN...         7   
                                       ACTIVIDADES HOSPITALARIAS                                  2   
                                       ACTIVIDADES INMOBILIARIAS (COMPRAVENTA, ALQUILE...        48   
                                       ACTIVIDADES JURIDICAS                                     14   
                                       ADIESTRAMIENTO, CUIDADO DE ANIMALES, RESIDENCIA...         1   
                                       ADMINISTRACION DE MERCADOS FINANCIEROS, INTERME...         2   
...                                                                                             ...   
Uso vivienda         9                 DESPACHO DE DIETISTAS                                      1   
                                       ENSEÑANZA NO REGLADA (DEPORTIVA Y RECREATIVA, C...         1   
                     10                COMERCIO AL POR MENOR DE PAN Y PRODUCTOS DE PAN...         1   
                                       LOCAL SIN ACTIVIDAD                                        1   
                                       OTRAS ACTIVIDADES DE CONSTRUCCION ESPECIALIZADA...         1   
                     11                ACTIVIDADES ADMINISTRATIVAS Y AUXILIARES DE OFI...         1   
                                       LOCAL SIN ACTIVIDAD                

In [428]:
nonulos = df_epi19[df_epi19['desc_epigrafe'].notnull()]
len(nonulos)

121889

In [36]:
len(nonulos)/len(df_epigrafes19)

0.746338386930858

In [38]:
df_e.groupby(['id_distrito_local','desc_epigrafe']).count()

id_local  \
id_distrito_local desc_epigrafe                                                  
1                 ACABADO DE EDIFICIOS (CARPINTERIA, REVOCAMIENTO...        12   
                  ACTIVIDADES ADMINISTRATIVAS Y AUXILIARES DE OFI...       166   
                  ACTIVIDADES ANEXAS AL TRANSPORTE                          13   
                  ACTIVIDADES AUXILIARES A SEGUROS Y FONDOS DE PE...         4   
                  ACTIVIDADES CINEMATOGRAFICAS, DE VIDEO Y DE TEL...        18   
                  ACTIVIDADES DE APOYO A LAS EMPRESAS N.C.O.P. (A...         2   
                  ACTIVIDADES DE BIBLIOTECAS, ARCHIVOS, MUSEOS Y ...        36   
                  ACTIVIDADES DE CLUBES DEPORTIVOS Y OTRAS ACTIVI...         2   
                  ACTIVIDADES DE CONSULTORIA DE GESTION EMPRESARIAL          5   
                  ACTIVIDADES DE CONTABILIDAD, TENEDURIA, AUDITOR...        18   
                  ACTIVIDADES DE CREACION, ARTISTICAS Y ESPECTACULOS        55   
                  ACTIVIDADES DE DISEÑO ESPECIALIZADO                       26   
                  ACTIVIDADES DE GESTION DE FONDOS                           1   
                  ACTIVIDADES DE GRABACION DE SONIDO Y EDICION MU...         4   
                  ACTIVIDADES DE LAS AGENCIAS DE COLOCACION                  2   
                  ACTIVIDADES DE LAS EMPRESAS DE TRABAJO TEMPORAL            2   
                  ACTIVIDADES DE LAS SEDES CENTRALES                        10   
                  ACTIVIDADES DE LIMPIEZA                                    8   
                  ACTIVIDADES DE LOS GIMNASIOS                              45   
                  ACTIVIDADES DE ORGANIZACIONES POLITICAS                    6   
                  ACTIVIDADES DE ORGANIZACIONES RELIGIOSAS                  78   
                  ACTIVIDADES DE ORGANIZACIONES Y ORGANISMOS EXTR...         2   
                  ACTIVIDADES DE PROGRAMACION Y EMISION DE RADIO ...         2   
                  ACTIVIDADES DE SEGURIDAD PRIVADA                           1   
                  ACTIVIDADES DE SERVICIOS SOCIALES SIN ALOJAMIEN...         8   
                  ACTIVIDADES HOSPITALARIAS                                  2   
                  ACTIVIDADES INMOBILIARIAS (COMPRAVENTA, ALQUILE...        49   
                  ACTIVIDADES JURIDICAS                                     14   
                  ADIESTRAMIENTO, CUIDADO DE ANIMALES, RESIDENCIA...         1   
                  ADMINISTRACION DE MERCADOS FINANCIEROS, INTERME...         2   
...                                                                        ...   
21                PUBLICIDAD, RELACIONES PUBLICAS Y ESTUDIOS DE M...         7   
                  RECOGIDA, TRATAMIENTO Y ELIMINACION DE RESIDUOS...         2   
                  REPARACION DE CALZADO                                      2   
                  REPARACION DE ORDENADORES Y EQUIPOS DE COMUNICA...         2   
                  RESTAURANTE                                               58   
                  RESTAURANTES DE COMIDA RAPIDA                             30   
                  SALONES DE RECREO Y DIVERSION Y OTRAS ACTIVIDAD...         3   
                  SEGUROS                                                    3   
                  SERIGRAFIA Y SERVICIOS DE PREIMPRESION Y PREPAR...         1   
                  SERVICIO DE PELUQUERIA                                    64   
                  SERVICIOS DE COMEDOR EN CENTROS EDUCATIVOS Y CE...        20   
                  SERVICIOS DE COMEDOR EN CENTROS PARA MAYORES               6   
                  SERVICIOS DE MENSAJERIA, ACTIVIDADES POSTALES Y...        15   
                  SERVICIOS DE SISTEMAS DE SEGURIDAD: VIGILANCIA ...         1   
                  SERVICIOS FOTOGRAFICOS                                     2   
                  SERVICIOS PARASANITARIOS (NATUROPATIA, ACUPUNTU...         3   
                  SERVICIOS TECNICOS DE ARQUITECTURA

In [47]:
df_epigrafes19[df_epigrafes19['id_distrito_local']== 1]\
.groupby(['desc_epigrafe']).count()

id_local  \
desc_epigrafe                                                  
ACABADO DE EDIFICIOS (CARPINTERIA, REVOCAMIENTO...        12   
ACTIVIDADES ADMINISTRATIVAS Y AUXILIARES DE OFI...       166   
ACTIVIDADES ANEXAS AL TRANSPORTE                          13   
ACTIVIDADES AUXILIARES A SEGUROS Y FONDOS DE PE...         4   
ACTIVIDADES CINEMATOGRAFICAS, DE VIDEO Y DE TEL...        18   
ACTIVIDADES DE APOYO A LAS EMPRESAS N.C.O.P. (A...         2   
ACTIVIDADES DE BIBLIOTECAS, ARCHIVOS, MUSEOS Y ...        36   
ACTIVIDADES DE CLUBES DEPORTIVOS Y OTRAS ACTIVI...         2   
ACTIVIDADES DE CONSULTORIA DE GESTION EMPRESARIAL          5   
ACTIVIDADES DE CONTABILIDAD, TENEDURIA, AUDITOR...        18   
ACTIVIDADES DE CREACION, ARTISTICAS Y ESPECTACULOS        55   
ACTIVIDADES DE DISEÑO ESPECIALIZADO                       26   
ACTIVIDADES DE GESTION DE FONDOS                           1   
ACTIVIDADES DE GRABACION DE SONIDO Y EDICION MU...         4   
ACTIVIDADES DE LAS AGENCIAS DE COLOCACION                  2   
ACTIVIDADES DE LAS EMPRESAS DE TRABAJO TEMPORAL            2   
ACTIVIDADES DE LAS SEDES CENTRALES                        10   
ACTIVIDADES DE LIMPIEZA                                    8   
ACTIVIDADES DE LOS GIMNASIOS                              45   
ACTIVIDADES DE ORGANIZACIONES POLITICAS                    6   
ACTIVIDADES DE ORGANIZACIONES RELIGIOSAS                  78   
ACTIVIDADES DE ORGANIZACIONES Y ORGANISMOS EXTR...         2   
ACTIVIDADES DE PROGRAMACION Y EMISION DE RADIO ...         2   
ACTIVIDADES DE SEGURIDAD PRIVADA                           1   
ACTIVIDADES DE SERVICIOS SOCIALES SIN ALOJAMIEN...         8   
ACTIVIDADES HOSPITALARIAS                                  2   
ACTIVIDADES INMOBILIARIAS (COMPRAVENTA, ALQUILE...        49   
ACTIVIDADES JURIDICAS                                     14   
ADIESTRAMIENTO, CUIDADO DE ANIMALES, RESIDENCIA...         1   
ADMINISTRACION DE MERCADOS FINANCIEROS, INTERME...         2   
...                                                      ...   
SEGUROS                                                   11   
SERIGRAFIA Y SERVICIOS DE PREIMPRESION Y PREPAR...         8   
SERVICIO DE PELUQUERIA                                   334   
SERVICIOS DE COMEDOR EN CENTROS EDUCATIVOS Y CE...        33   
SERVICIOS DE COMEDOR EN CENTROS PARA MAYORES              22   
SERVICIOS DE INFORMACION: PROCESO DE DATOS, POR...         1   
SERVICIOS DE MENSAJERIA, ACTIVIDADES POSTALES Y...        23   
SERVICIOS DE PREPARACI0N DE COMIDAS EN HOSPITALES          1   
SERVICIOS FOTOGRAFICOS                                     7   
SERVICIOS INTEGRALES A EDIFICIOS E INSTALACIONES           4   
SERVICIOS PARASANITARIOS (NATUROPATIA, ACUPUNTU...        10   
SERVICIOS TECNICOS DE ARQUITECTURA E INGENIERIA...        33   
SEX-SHOP                                                  11   
SIN ASIGNAR                                               12   
SITUADOS: COMPLEMENTOS, BISUTERIA Y ARTESANIA             16   
SITUADOS: FLORES Y PLANTAS                                 1   
TABERNA                                                   73   
TALLER DE MONTAJE DE ACCESORIOS PARA EL AUTOMOVIL          1   
TALLER DE REPARACION DE AUTOMOVILES ESPECIALIZA...        10   
TALLER DE REPARACION DE AUTOMOVILES ESPECIALIZA...         9   
TAPICERIA                                                  9   
TEATRO Y ACTIVIDADES ESCENICAS REALIZADAS EN DI...        35   
TELECOMUNICACIONES                                         9   
TIENDA DE CONVENIENCIA (24H)                               4   
TRANSPORTE TERRESTRE URBANO (AUTOBUS, METRO, TA...         2   
TRATAMIENTO HIGIENICO DE ANIMALES (PELUQUERIAS)           11   
VENDEDOR AMBULANTE DE ALIMENTOS PREPARADOS PARA...         2   
VENTA DE MOTOCICLETAS                                      2   
VIDEOCLUB                                                  6   
VIVIENDAS TURISTICAS                                       2   

                   

In [53]:
grouped = df_epigrafes19.groupby(['id_distrito_local'])

In [57]:
grouped.agg('count')

id_local  desc_distrito_local  id_barrio_local  \
id_distrito_local                                                   
1                     14338                14338            14338   
2                      6576                 6576             6576   
3                      4606                 4606             4606   
4                      9420                 9420             9420   
5                      7647                 7647             7647   
6                     10559                10559            10559   
7                      8398                 8398             8398   
8                      8519                 8519             8519   
9                      5389                 5389             5389   
10                    10472                10472            10472   
11                    13431                13431            13431   
12                     6328                 6328             6328   
13                    11634                11634            11634   
14                     2882                 2882             2882   
15                    11994                11994            11994   
16                     6963                 6963             6963   
17                     7792                 7792             7792   
18                     5460                 5460             5460   
19                     2264                 2264             2264   
20                     6386                 6386             6386   
21                     2258                 2258             2258   

                   desc_barrio_local  cod_barrio_local  \
id_distrito_local                                        
1                              14338                 0   
2                               6576                 0   
3                               4606                 0   
4                               9420                 0   
5                               7647                 0   
6                              10559                 0   
7                               8398                 0   
8                               8519                 0   
9                               5389                 0   
10                             10472                 0   
11                             13431                 0   
12                              6328                 0   
13                             11634                 0   
14                              2882                 0   
15                             11994                 0   
16                              6963                 0   
17                              7792                 0   
18                              5460                 0   
19                              2264                 0   
20                              6386                 0   
21                              2258                 0   

                   id_seccion_censal_local  desc_seccion_censal_local  \
id_distrito_local                                                       
1                                        0                      14338   
2                                        0                       6576   
3                                        0                       4606   
4                                        0                       9420   
5                                        0                       7647   
6                                        0                      10559   
7                                        0                       8398   
8                                        0                       8519   
9                                        0                       5389   
10                                       0                      10472   
11                                       0                      13431   
12                                       0                       6328   
13                                       0                      11634   
1

In [61]:
grouped_notnul = df_epigrafes19[df_epigrafes19['desc_epigrafe'].notnull()].groupby(['id_distrito_local'])

In [63]:
grouped_notnul.agg('count')

id_local  desc_distrito_local  id_barrio_local  \
id_distrito_local                                                   
1                     12282                12282            12282   
2                      5553                 5553             5553   
3                      4084                 4084             4084   
4                      8599                 8599             8599   
5                      6444                 6444             6444   
6                      7402                 7402             7402   
7                      7529                 7529             7529   
8                      6378                 6378             6378   
9                      4474                 4474             4474   
10                     6905                 6905             6905   
11                     8719                 8719             8719   
12                     4335                 4335             4335   
13                     6983                 6983             6983   
14                     2281                 2281             2281   
15                     7909                 7909             7909   
16                     4597                 4597             4597   
17                     5193                 5193             5193   
18                     3981                 3981             3981   
19                     1666                 1666             1666   
20                     4791                 4791             4791   
21                     1784                 1784             1784   

                   desc_barrio_local  cod_barrio_local  \
id_distrito_local                                        
1                              12282                 0   
2                               5553                 0   
3                               4084                 0   
4                               8599                 0   
5                               6444                 0   
6                               7402                 0   
7                               7529                 0   
8                               6378                 0   
9                               4474                 0   
10                              6905                 0   
11                              8719                 0   
12                              4335                 0   
13                              6983                 0   
14                              2281                 0   
15                              7909                 0   
16                              4597                 0   
17                              5193                 0   
18                              3981                 0   
19                              1666                 0   
20                              4791                 0   
21                              1784                 0   

                   id_seccion_censal_local  desc_seccion_censal_local  \
id_distrito_local                                                       
1                                        0                      12282   
2                                        0                       5553   
3                                        0                       4084   
4                                        0                       8599   
5                                        0                       6444   
6                                        0                       7402   
7                                        0                       7529   
8                                        0                       6378   
9                                        0                       4474   
10                                       0                       6905   
11                                       0                       8719   
12                                       0                       4335   
13                                       0                       6983   
1

In [64]:
tablon = pd.merge(df_epigrafes19,df_locales19,on='id_local')

In [65]:
tablon.head()

id_local  id_distrito_local_x desc_distrito_local_x  id_barrio_local_x  \
0  280052883                   11  CARABANCHEL                        1102   
1  280052899                   11  CARABANCHEL                        1102   
2  280052901                   11  CARABANCHEL                        1102   
3  280052904                   11  CARABANCHEL                        1102   
4  280052908                   11  CARABANCHEL                        1102   

    desc_barrio_local_x  cod_barrio_local_x  id_seccion_censal_local_x  \
0  OPAÑEL                               NaN                        NaN   
1  OPAÑEL                               NaN                        NaN   
2  OPAÑEL                               NaN                        NaN   
3  OPAÑEL                               NaN                        NaN   
4  OPAÑEL                               NaN                        NaN   

   desc_seccion_censal_local_x coordenada_x_local_x coordenada_y_local_x  \
0                           22            439084,59           4471128,53   
1                           24            438715,59           4471117,53   
2                           24            438728,59           4471142,53   
3                           24            438711,59           4471159,53   
4                           26            438759,59           4470827,53   

                    ...                    cal_acceso_y  \
0                   ...                                   
1                   ...                                   
2                   ...                                   
3                   ...                                   
4                   ...                                   

  coordenada_x_agrupacion_y  coordenada_y_agrup_y id_agrupacion_y  \
0                       NaN                   NaN             NaN   
1                       NaN                   NaN             NaN   
2                       NaN                   NaN             NaN   
3                       NaN                   NaN             NaN   
4                       NaN                   NaN             NaN   

   nombre_agrupacion_y id_tipo_agrup_y desc_tipo_agrup_y  \
0                  NaN             NaN               NaN   
1                  NaN             NaN               NaN   
2                  NaN             NaN               NaN   
3                  NaN             NaN               NaN   
4                  NaN             NaN               NaN   

   id_planta_agrupado_y  id_local_agrupado_y  \
0                    PB                  NaN   
1                    PB                  NaN   
2                    PB                  NaN   
3                    PB                  NaN   
4                    PB                  NaN   

                                 rotulo_y  
0                       TALLER AUTOMASTER  
1                                      SR  
2                                 INFYNSA  
3  RESTAURANTE OSUNA CAFETERIA CERVECERIA  
4                       LIMPIEZA MADROÑAL  

[5 rows x 85 columns]

In [66]:
d3 = pd.DataFrame(tablon.dtypes)
d3.reset_index()

index        0
0                      id_local    int64
1           id_distrito_local_x    int64
2         desc_distrito_local_x   object
3             id_barrio_local_x    int64
4           desc_barrio_local_x   object
5            cod_barrio_local_x  float64
6     id_seccion_censal_local_x  float64
7   desc_seccion_censal_local_x    int64
8          coordenada_x_local_x   object
9          coordenada_y_local_x   object
10       id_tipo_acceso_local_x  float64
11     desc_tipo_acceso_local_x   object
12         id_situacion_local_x  float64
13       desc_situacion_local_x   object
14           id_vial_edificio_x    int64
15        clase_vial_edificio_x   object
16         desc_vial_edificio_x   object
17            id_ndp_edificio_x    int64
18      id_clase_ndp_edificio_x    int64
19               nom_edificio_x   object
20               num_edificio_x    int64
21               cal_edificio_x   object
22        secuencial_local_PC_x    int64
23             id_vial_acceso_x  float64
24          clase_vial_acceso_x   object
25           desc_vial_acceso_x   object
26              id_ndp_acceso_x    int64
27        id_clase_ndp_acceso_x    int64
28                 nom_acceso_x   object
29                 num_acceso_x    int64
..                          ...      ...
55       id_tipo_acceso_local_y  float64
56     desc_tipo_acceso_local_y   object
57         id_situacion_local_y    int64
58       desc_situacion_local_y   object
59           id_vial_edificio_y  float64
60        clase_vial_edificio_y   object
61         desc_vial_edificio_y   object
62            id_ndp_edificio_y    int64
63      id_clase_ndp_edificio_y    int64
64               nom_edificio_y   object
65               num_edificio_y    int64
66               cal_edificio_y   object
67        secuencial_local_PC_y    int64
68             id_vial_acceso_y  float64
69          clase_vial_acceso_y   object
70           desc_vial_acceso_y   object
71              id_ndp_acceso_y    int64
72        id_clase_ndp_acceso_y    int64
73                 nom_acceso_y   object
74                 num_acceso_y    int64
75                 cal_acceso_y   object
76    coordenada_x_agrupacion_y   object
77         coordenada_y_agrup_y   object
78              id_agrupacion_y  float64
79          nombre_agrupacion_y   object
80              id_tipo_agrup_y  float64
81            desc_tipo_agrup_y   object
82         id_planta_agrupado_y   object
83          id_local_agrupado_y   object
84                     rotulo_y   object

[85 rows x 2 columns]

In [68]:
d3.reset_index().to_csv('variables_tablon.csv')

In [69]:
tablon.to_csv('tablon_2019.csv')

In [67]:
pwd

'/home/dsc/Python_notebooks/TFM/Ciudadmadrid/censolocales'

In [78]:
import seaborn as sns

In [80]:
df_epigrafes19.colums = [column.strip for column in df_epigrafes19.columns]
df_epigrafes19.head()

id_local  id_distrito_local   desc_distrito_local  id_barrio_local  \
0  280052883                 11  CARABANCHEL                      1102   
1  280052899                 11  CARABANCHEL                      1102   
2  280052901                 11  CARABANCHEL                      1102   
3  280052904                 11  CARABANCHEL                      1102   
4  280052908                 11  CARABANCHEL                      1102   

      desc_barrio_local  cod_barrio_local  id_seccion_censal_local  \
0  OPAÑEL                             NaN                      NaN   
1  OPAÑEL                             NaN                      NaN   
2  OPAÑEL                             NaN                      NaN   
3  OPAÑEL                             NaN                      NaN   
4  OPAÑEL                             NaN                      NaN   

   desc_seccion_censal_local coordenada_x_local coordenada_y_local  \
0                         22          439084,59         4471128,53   
1                         24          438715,59         4471117,53   
2                         24          438728,59         4471142,53   
3                         24          438711,59         4471159,53   
4                         26          438759,59         4470827,53   

                         ...                          desc_tipo_agrup  \
0                        ...                                      NaN   
1                        ...                                      NaN   
2                        ...                                      NaN   
3                        ...                                      NaN   
4                        ...                                      NaN   

  id_planta_agrupado  id_local_agrupado  \
0                 PB                NaN   
1                 PB                NaN   
2                 PB                NaN   
3                 PB                NaN   
4                 PB                NaN   

                                   rotulo  id_seccion  \
0                       TALLER AUTOMASTER           G   
1                                      SR           F   
2                                 INFYNSA           G   
3  RESTAURANTE OSUNA CAFETERIA CERVECERIA           I   
4                       LIMPIEZA MADROÑAL           N   

                                        desc_seccion id_division  \
0  COMERCIO AL POR MAYOR Y AL POR MENOR; REPARACI...          45   
1                                       CONSTRUCCI0N          43   
2  COMERCIO AL POR MAYOR Y AL POR MENOR; REPARACI...          46   
3                                         HOSTELERIA          56   
4  ACTIVIDADES ADMINISTRATIVAS Y SERVICIOS AUXLIARES          81   

                                       desc_division  id_epigrafe  \
0  VENTA Y REPARACI0N DE VEHICULOS DE MOTOR Y MOT...       452002   
1  ACTIVIDADES DE CONSTRUCCI0N ESPECIALIZADA Y AC...       432001   
2  COMERCIO AL POR MAYOR E INTERMEDIARIOS DEL COM...       461801   
3                     SERVICIOS DE COMIDAS Y BEBIDAS       561004   
4  SERVICIOS A EDIFICIOS Y ACTIVIDADES DE JARDINERIA       812001   

                                       desc_epigrafe  
0  TALLER DE REPARACION DE AUTOMOVILES ESPECIALIZ...  
1  INSTALACIONES ELECTRICAS, DE FONTANERIA Y OTRA...  
2  INTERMEDIARIOS DEL COMERCIO ESPECIALIZADOS EN ...  
3                                    BAR RESTAURANTE  
4                            ACTIVIDADES DE LIMPIEZA  

[5 rows x 46 columns]

In [ ]:
sns.jointplot(data=df_epigrafes19, x='id_local',y='id_barrio_local',kind='kde');

In [85]:
pd.options.display.max_columns = None

In [88]:
tablon.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 163316 entries, 0 to 163315
Data columns (total 85 columns):
id_local                       163316 non-null int64
id_distrito_local_x            163316 non-null int64
desc_distrito_local_x          163316 non-null object
id_barrio_local_x              163316 non-null int64
desc_barrio_local_x            163316 non-null object
cod_barrio_local_x             0 non-null float64
id_seccion_censal_local_x      0 non-null float64
desc_seccion_censal_local_x    163316 non-null int64
coordenada_x_local_x           163316 non-null object
coordenada_y_local_x           163316 non-null object
id_tipo_acceso_local_x         0 non-null float64
desc_tipo_acceso_local_x       163316 non-null object
id_situacion_local_x           0 non-null float64
desc_situacion_local_x         163316 non-null object
id_vial_edificio_x             163316 non-null int64
clase_vial_edificio_x          163316 non-null object
desc_vial_edificio_x           163316 non-null

In [91]:
tablon.isnull().sum()

id_local                            0
id_distrito_local_x                 0
desc_distrito_local_x               0
id_barrio_local_x                   0
desc_barrio_local_x                 0
cod_barrio_local_x             163316
id_seccion_censal_local_x      163316
desc_seccion_censal_local_x         0
coordenada_x_local_x                0
coordenada_y_local_x                0
id_tipo_acceso_local_x         163316
desc_tipo_acceso_local_x            0
id_situacion_local_x           163316
desc_situacion_local_x              0
id_vial_edificio_x                  0
clase_vial_edificio_x               0
desc_vial_edificio_x                0
id_ndp_edificio_x                   0
id_clase_ndp_edificio_x             0
nom_edificio_x                      0
num_edificio_x                      0
cal_edificio_x                      0
secuencial_local_PC_x               0
id_vial_acceso_x               163316
clase_vial_acceso_x                 0
desc_vial_acceso_x                  0
id_ndp_acces

In [312]:
abierto = df_local19_clean['desc_situacion_local'] == 'Abierto'
cerrado = df_local19_clean['desc_situacion_local'] == 'Cerrado'
obras = df_local19_clean['desc_situacion_local'] == 'Obras'
baja = df_local19_clean['desc_situacion_local'] == 'Baja'
bajar = df_local19_clean['desc_situacion_local'] == 'BajaR'
vivienda = df_local19_clean['desc_situacion_local'] == 'Uso vivienda'
df_local19_clean['cerrado19'] = [cerrado | baja].id_distrito_local.count()

35860